# Importing data and data pre processing


In [ ]:
!pip install phply

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
import sqlite3
import pandas as pd
cnx = sqlite3.connect("/content/drive/MyDrive/xss-sqli-invuln-big--dataset-big-notmodified.db")
df = pd.read_sql_query("SELECT * FROM datasets", cnx)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 108505 entries, 0 to 108504
Data columns (total 4 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   test_case  108505 non-null  object
 1   code       108505 non-null  object
 2   vuln_type  108505 non-null  object
 3   name       108505 non-null  object
dtypes: object(4)
memory usage: 3.3+ MB


In [ ]:
df = df.drop(['test_case', 'name'], axis=1)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 108505 entries, 0 to 108504
Data columns (total 2 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   code       108505 non-null  object
 1   vuln_type  108505 non-null  object
dtypes: object(2)
memory usage: 1.7+ MB


In [ ]:
df['vuln_type'].value_counts()

vuln_type
Not Vulnerable              59800
XSS Vulnerable              28555
SQL Injection Vulnerable    20150
Name: count, dtype: int64

In [ ]:
df.drop_duplicates(subset = ['code','vuln_type'],inplace = True) # hapus duplikat data

In [ ]:
df['vuln_type'].value_counts()

vuln_type
Not Vulnerable              47967
XSS Vulnerable              22246
SQL Injection Vulnerable    14068
Name: count, dtype: int64

Jumlah label data tidak seimbang. maka under sampling di lakukan

In [ ]:
import sqlite3

# Connect to (or create) the new SQLite database file
conn = sqlite3.connect('/content/drive/MyDrive/xss-sqli-invuln-big--dataset-big--dupes-cleaned.db')

# Write the DataFrame to the database
df.to_sql('datasets', conn, if_exists='replace', index=False)

# Close the connection
conn.close()

## Undersampling

In [ ]:
import sqlite3
import pandas as pd
cnx = sqlite3.connect("/content/drive/MyDrive/xss-sqli-invuln-big--dataset-big--dupes-cleaned.db")
df = pd.read_sql_query("SELECT * FROM datasets", cnx)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 84281 entries, 0 to 84280
Data columns (total 2 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   code       84281 non-null  object
 1   vuln_type  84281 non-null  object
dtypes: object(2)
memory usage: 1.3+ MB


In [ ]:
df['vuln_type'].value_counts()

vuln_type
Not Vulnerable              47967
XSS Vulnerable              22246
SQL Injection Vulnerable    14068
Name: count, dtype: int64

In [ ]:
df.drop_duplicates(subset = ['code','vuln_type'],inplace = True) # hapus duplikat data

In [ ]:
df['vuln_type'].value_counts()

vuln_type
Not Vulnerable              47967
XSS Vulnerable              22246
SQL Injection Vulnerable    14068
Name: count, dtype: int64

tidak ada duplikat data lagi

In [ ]:
# undersampling

#sqli
df_other = pd.read_sql_query("SELECT * FROM datasets where vuln_type = 'SQL Injection Vulnerable' limit 12000", cnx)
df_other['vuln_type'].value_counts()

# secure
df_sec = pd.read_sql_query("SELECT * FROM datasets where vuln_type = 'Not Vulnerable' limit 12000 ", cnx)
df_sec['vuln_type'].value_counts()

# xss
df_xss = pd.read_sql_query("SELECT * FROM datasets where vuln_type = 'XSS Vulnerable' limit 12000", cnx)
df_xss['vuln_type'].value_counts()

#join = [df_other, df_xss, df_sql]
join = [df_other, df_xss, df_sec]
df_6k = pd.concat(join)
df_6k = df_6k.reset_index(drop=True)
#df_6k['potential_vuln'].value_counts()
df_6k['code'].isnull().value_counts()

df = df_6k

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 36000 entries, 0 to 35999
Data columns (total 2 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   code       36000 non-null  object
 1   vuln_type  36000 non-null  object
dtypes: object(2)
memory usage: 562.6+ KB


In [ ]:
df['vuln_type'].value_counts()

vuln_type
SQL Injection Vulnerable    12000
XSS Vulnerable              12000
Not Vulnerable              12000
Name: count, dtype: int64

## Data cleansing (hapus html, komen, dan format ulang)

In [ ]:
import re

def remove_html_and_content(code: str) -> str:
    html_tags = [
    "a", "abbr", "address", "area", "article", "aside", "audio", "b", "base",
    "bdi", "bdo", "blockquote", "body", "br", "button", "canvas", "caption",
    "cite", "code", "col", "colgroup", "data", "datalist", "dd", "del",
    "details", "dfn", "dialog", "div", "dl", "dt", "em", "embed", "fieldset",
    "figcaption", "figure", "footer", "form", "h1", "h2", "h3", "h4", "h5",
    "h6", "head", "header", "hr", "html", "i", "iframe", "img", "input",
    "ins", "kbd", "label", "legend", "li", "link", "main", "map", "mark",
    "meta", "meter", "nav", "noscript", "object", "ol", "optgroup", "option",
    "output", "p", "param", "picture", "pre", "progress", "q", "rp", "rt",
    "ruby", "s", "samp", "script", "section", "select", "small", "source",
    "span", "strong", "style", "sub", "summary", "sup", "table", "tbody",
    "td", "template", "textarea", "tfoot", "th", "thead", "time", "title",
    "tr", "track", "u", "ul", "var", "video", "wbr"]
    tags_pattern = '|'.join(html_tags)

    content_block_pattern = re.compile(
        rf'<(?:{tags_pattern})\b[^>]*?>.*?</(?:{tags_pattern})>',
        flags=re.IGNORECASE | re.DOTALL
    )

    matches = content_block_pattern.findall(code)
    #print(matches)
    for match in matches:
        if ".$" not in match:
            code = code.replace(match.strip(), '')

    #code = content_block_pattern.sub('', code)

    self_closing_pattern = re.compile(
        rf'<(?:{tags_pattern})\b[^>]*/?>',
        flags=re.IGNORECASE
    )

    matches = self_closing_pattern.findall(code)
    for match in matches:
        if ".$" not in match:
            code = code.replace(match.strip(), '')

    #code = self_closing_pattern.sub('', code)

    return code.strip()

def process_php_tokenized(code: str) -> str:
    # 1. Ambil semua blok <?php ... ?> dan <?= ... ?> (multiline)
    php_blocks = re.findall(r'(<\?(?:php|=)(?:.|\n)*?\?>)', code)
    php_code = '\n'.join(php_blocks)

    # 2. Auto-fix jika jumlah open > close
    open_count = len(re.findall(r'<\?(php|=)', php_code, re.IGNORECASE))
    close_count = len(re.findall(r'\?>', php_code))
    if open_count > close_count:
        php_code += '\n' + '?>' * (open_count - close_count)

    # # 3. HAPUS KOMENTAR PHP
    # # Hapus block comment /* ... */ dan /** ... */
    php_code = re.sub(r'/\*[\s\S]*?\*/', '', php_code)

    # # Hapus single-line comment // dan #
    php_code = re.sub(r'//.*', '', php_code)      # // inline
    php_code = re.sub(r'#.*', '', php_code)       # # inline

    php_code = remove_html_and_content(php_code)

    # # 4. Bersihin karakter aneh dari copy-paste
    # php_code = php_code.replace("”", '"').replace("‘", "'").replace("’", "'")
    # php_code = php_code.replace("—", "-").replace("–", "-").replace('“', '"')
    # php_code = php_code.replace('\\}', '}').replace('\\{', '{')
    # php_code = php_code.replace('{\\', '{').replace('\\}', '}')
    # php_code = php_code.replace("\n'", "'").replace('\n"', '"')

    # # 5. Normalisasi spacing (opsional)
    # php_code = php_code.replace('(', ' ( ').replace(')', ' ) ')
    # php_code = php_code.replace('[', ' [ ').replace(']', ' ] ')
    # php_code = php_code.replace("';", "' ; ")
    # php_code = php_code.replace("($_POST[", "( $_POST[")
    # php_code = php_code.replace('{', "{\n").replace('}', "}\n")
    # php_code = re.sub(r'\n\n+', '\n', php_code)

    return php_code.strip()


In [ ]:
#df['tok_fin'] = df['code'].apply(token_final) # token
df['cleaned'] = df['code'].apply(process_php_tokenized) # joined token

In [ ]:
print(df['code'][0])

<!--
# Sample information

Patterns:
- Source: filter_input_prm__<c>(INPUT_GET)_<s>(t)_<c>(FILTER_UNSAFE_RAW) ==> Filters:[]
- Sanitization: str_replace_prm__<s>(\w)_<s>() ==> Filters:[]
- Filters complete: Filters:[]
- Dataflow: assignment
- Context: sql_quotes
- Sink: mysqli_multi_query_prm__<$>(db)

State:
- State: Bad
- Exploitable: Yes


# Exploit description

1. Escape quotes with "
2. No enclosure and special chars are allowed -> SQL injection
-->
<?php
# Init
$servername = "mysql";
$username = "username";
$password = "password";
$dbName = "myDB";
$db = new mysqli($servername, $username, $password, $dbName);


# Sample
$tainted = filter_input(INPUT_GET, "t", FILTER_UNSAFE_RAW);
$sanitized = str_replace(" ", "", $tainted);
$dataflow = $sanitized;
$context = (("SELECT * FROM users WHERE password =\"" . $dataflow) . "\";");
mysqli_multi_query($db, $context);
$results = $db->use_result();
while(($row = $results->fetch_row()))
{
  echo(htmlentities(print_r($row, true)));
}

?>


In [ ]:
print(df['cleaned'][0])

<?php

$servername = "mysql";
$username = "username";
$password = "password";
$dbName = "myDB";
$db = new mysqli($servername, $username, $password, $dbName);



$tainted = filter_input(INPUT_GET, "t", FILTER_UNSAFE_RAW);
$sanitized = str_replace(" ", "", $tainted);
$dataflow = $sanitized;
$context = (("SELECT * FROM users WHERE password =\"" . $dataflow) . "\";");
mysqli_multi_query($db, $context);
$results = $db->use_result();
while(($row = $results->fetch_row()))
{
  echo(htmlentities(print_r($row, true)));
}

?>


In [ ]:
a = """

<?php
/**
 * Copyright (C) 2007,2008  Arie Nugraha (dicarve@yahoo.com)
 *
 * This program is free software; you can redistribute it and/or modify
 * it under the terms of the GNU General Public License as published by
 * the Free Software Foundation; either version 3 of the License, or
 * (at your option) any later version.
 *
 * This program is distributed in the hope that it will be useful,
 * but WITHOUT ANY WARRANTY; without even the implied warranty of
 * MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
 * GNU General Public License for more details.
 *
 * You should have received a copy of the GNU General Public License
 * along with this program; if not, write to the Free Software
 * Foundation, Inc., 51 Franklin Street, Fifth Floor, Boston, MA  02110-1301  USA
 *
 */

/* Collection Type Management section */

// key to authenticate
define('INDEX_AUTH', '1');
// key to get full database access
define('DB_ACCESS', 'fa');

// main system configuration
require '../../../sysconfig.inc.php';
// IP based access limitation
require LIB.'ip_based_access.inc.php';
do_checkIP('smc');
do_checkIP('smc-masterfile');
// start the session
require SB.'admin/default/session.inc.php';
require SB.'admin/default/session_check.inc.php';
require SIMBIO.'simbio_GUI/table/simbio_table.inc.php';
require SIMBIO.'simbio_GUI/form_maker/simbio_form_table_AJAX.inc.php';
require SIMBIO.'simbio_GUI/paging/simbio_paging.inc.php';
require SIMBIO.'simbio_DB/datagrid/simbio_dbgrid.inc.php';
require SIMBIO.'simbio_DB/simbio_dbop.inc.php';

// privileges checking
$can_read = utility::havePrivilege('master_file', 'r');
$can_write = utility::havePrivilege('master_file', 'w');

if (!$can_read) {
    die('<div class="errorBox">'.__('You don\'t have enough privileges to view this section').'</div>');
}

/* RECORD OPERATION */
if (isset($_POST['saveData'])) {
    $collTypeName = trim(strip_tags($_POST['collTypeName']));
    // check form validity
    if (empty($collTypeName)) {
        utility::jsToastr(__('Collection Type'),__('Collection type name can\'t be empty'),'error');
        exit();
    } else {
        $data['coll_type_name'] = $dbs->escape_string($collTypeName);
        $data['input_date'] = date('Y-m-d');
        $data['last_update'] = date('Y-m-d');

        // create sql op object
        $sql_op = new simbio_dbop($dbs);
        if (isset($_POST['updateRecordID'])) {
            /* UPDATE RECORD MODE */
            // remove input date
            unset($data['input_date']);
            // filter update record ID
            $updateRecordID = (integer)$_POST['updateRecordID'];
            // update the data
            $update = $sql_op->update('mst_coll_type', $data, 'coll_type_id='.$updateRecordID);
            if ($update) {
                utility::jsToastr(__('Collection Type'),__('Colllection Type Data Successfully Updated'),'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(parent.jQuery.ajaxHistory[0].url);</script>';
            } else { utility::jsToastr(__('Collection Type'),__('Colllection Type Data FAILED to Updated. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error); }
            exit();
        } else {
            /* INSERT RECORD MODE */
            // insert the data
            $insert = $sql_op->insert('mst_coll_type', $data);
            if ($insert) {
                utility::jsToastr(__('Collection Type'),__('New Colllection Type Data Successfully Saved'),'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
            } else { utility::jsToastr(__('Collection Type'),__('Author Data FAILED to Save. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error,'error'); }
            exit();
        }
    }
    exit();
} else if (isset($_POST['itemID']) AND !empty($_POST['itemID']) AND isset($_POST['itemAction'])) {
    if (!($can_read AND $can_write)) {
        die();
    }
    /* DATA DELETION PROCESS */
    $sql_op = new simbio_dbop($dbs);
    $failed_array = array();
    $error_num = 0;
    if (!is_array($_POST['itemID'])) {
        // make an array
        $_POST['itemID'] = array((integer)$_POST['itemID']);
    }
    // loop array
    foreach ($_POST['itemID'] as $itemID) {
        $itemID = (integer)$itemID;
        // check if this item data still have an item
        $item_q = $dbs->query('SELECT ct.coll_type_name, COUNT(item_id) FROM item AS i
            LEFT JOIN mst_coll_type AS ct ON i.coll_type_id=ct.coll_type_id
            WHERE i.coll_type_id='.$itemID.' GROUP BY i.coll_type_id');
        $item_d = $item_q->fetch_row();
        if ($item_d[1] < 1) {
            if (!$sql_op->delete('mst_coll_type', "coll_type_id=$itemID")) {
                $error_num++;
            }
        } else {
            $still_have_item[] = sprintf(__('Collection type %s still used by %s items'),$item_d[0],$item_d[1]);
            $error_num++;
        }
    }

    if ($still_have_item) {
        $undeleted_coll_types = '';
        foreach ($still_have_item as $coll_type) {
            $undeleted_coll_types .= $coll_type."\n";
        }
        utility::jsToastr(__('Collection Type'),__('Below data can not be deleted:').$undeleted_coll_types,'error');
        exit();
    }
    // error alerting
    if ($error_num == 0) {
        utility::jsToastr(__('Collection Type'),__('All Data Successfully Deleted'),'success');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    } else {
        utility::jsToastr(__('Collection Type'),__('Some or All Data NOT deleted successfully!\nPlease contact system administrator'),'warning');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    }
    exit();
}
/* RECORD OPERATION END */

/* search form */
?>
<div class="menuBox">
<div class="menuBoxInner masterFileIcon">
	<div class="per_title">
	    <h2><?php echo __('Collection Type'); ?></h2>
  </div>
	<div class="sub_section">
	  <div class="btn-group">
      <a href="<?php echo MWB; ?>master_file/coll_type.php" class="btn btn-default"><?php echo __('Collection Type List'); ?></a>
      <a href="<?php echo MWB; ?>master_file/coll_type.php?action=detail" class="btn btn-default"><?php echo __('Add New Collection Type'); ?></a>
	  </div>
    <form name="search" action="<?php echo MWB; ?>master_file/coll_type.php" id="search" method="get" class="form-inline"><?php echo __('Search'); ?>
    <input type="text" name="keywords" class="form-control col-md-3" />
    <input type="submit" id="doSearch" value="<?php echo __('Search'); ?>" class="s-btn btn btn-default" />
    </form>
  </div>
</div>
</div>
<?php
/* search form end */
/* main content */
if (isset($_POST['detail']) OR (isset($_GET['action']) AND $_GET['action'] == 'detail')) {
    if (!($can_read AND $can_write)) {
        die('<div class="errorBox">'.__('You don\'t have enough privileges to view this section').'</div>');
    }
    $itemID = (integer)isset($_POST['itemID'])?$_POST['itemID']:0;
    $rec_q = $dbs->query("SELECT * FROM mst_coll_type WHERE coll_type_id=$itemID");
    $rec_d = $rec_q->fetch_assoc();

    // create new instance
    $form = new simbio_form_table_AJAX('mainForm', $_SERVER['PHP_SELF'].'?'.$_SERVER['QUERY_STRING'], 'post');
    $form->submit_button_attr = 'name="saveData" value="'.__('Save').'" class="s-btn btn btn-default"';

    // form table attributes
    $form->table_attr = 'id="dataList" class="s-table table"';
    $form->table_header_attr = 'class="alterCell font-weight-bold"';
    $form->table_content_attr = 'class="alterCell2"';

    // edit mode flag set
    if ($rec_q->num_rows > 0) {
        $form->edit_mode = true;
        // record ID for delete process
        $form->record_id = $itemID;
        // form record title
        $form->record_title = $rec_d['coll_type_name'];
        // submit button attribute
        $form->submit_button_attr = 'name="saveData" value="'.__('Update').'" class="s-btn btn btn-primary"';
    }

    /* Form Element(s) */
    // coll_type_name
    $form->addTextField('text', 'collTypeName', __('Collection Type').'*', $rec_d['coll_type_name']??'', 'style="width: 60%;" class="form-control"');

    // edit mode messagge
    if ($form->edit_mode) {
        echo '<div class="infoBox">'.__('You are going to edit collection type data').' : <b>'.$rec_d['coll_type_name'].'</b>  <br />'.__('Last Update').' '.$rec_d['last_update'].'</div>'; //mfc
    }
    // print out the form object
    echo $form->printOut();
} else {
    /* COLLECTION TYPE LIST */
    // table spec
    $table_spec = 'mst_coll_type AS ct';

    // create datagrid
    $datagrid = new simbio_datagrid();
    if ($can_read AND $can_write) {
        $datagrid->setSQLColumn('ct.coll_type_id', 'ct.coll_type_name AS \''.__('Collection Type').'\'', 'ct.last_update AS \''.__('Last Update').'\'');
    } else {
        $datagrid->setSQLColumn('ct.coll_type_name AS \''.__('Collection Type').'\'', 'ct.last_update AS \''.__('Last Update').'\'');
    }
    $datagrid->setSQLorder('coll_type_name ASC');

    // change the record order
    if (isset($_GET['fld']) AND isset($_GET['dir'])) {
        $datagrid->setSQLorder("'".urldecode($_GET['fld'])."' ".$dbs->escape_string($_GET['dir']));
    }

    // is there any search
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
       $keywords = utility::filterData('keywords', 'get', true, true, true);
       $datagrid->setSQLCriteria("ct.coll_type_name LIKE '%$keywords%'");
    }

    // set table and table header attributes
    $datagrid->table_attr = 'id="dataList" class="s-table table"';
    $datagrid->table_header_attr = 'class="dataListHeader" style="font-weight: bold;"';
    // set delete proccess URL
    $datagrid->chbox_form_URL = $_SERVER['PHP_SELF'];

    // put the result into variables
    $datagrid_result = $datagrid->createDataGrid($dbs, $table_spec, 20, ($can_read AND $can_write));
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
        $msg = str_replace('{result->num_rows}', $datagrid->num_rows, __('Found <strong>{result->num_rows}</strong> from your keywords')); //mfc
        echo '<div class="infoBox">'.$msg.' : "'.htmlspecialchars($_GET['keywords']).'"</div>';
    }

    echo $datagrid_result;
}
/* main content end */
"""
print(process_php_tokenized(a))

<?php





define('INDEX_AUTH', '1');

define('DB_ACCESS', 'fa');


require '../../../sysconfig.inc.php';

require LIB.'ip_based_access.inc.php';
do_checkIP('smc');
do_checkIP('smc-masterfile');

require SB.'admin/default/session.inc.php';
require SB.'admin/default/session_check.inc.php';
require SIMBIO.'simbio_GUI/table/simbio_table.inc.php';
require SIMBIO.'simbio_GUI/form_maker/simbio_form_table_AJAX.inc.php';
require SIMBIO.'simbio_GUI/paging/simbio_paging.inc.php';
require SIMBIO.'simbio_DB/datagrid/simbio_dbgrid.inc.php';
require SIMBIO.'simbio_DB/simbio_dbop.inc.php';


$can_read = utility::havePrivilege('master_file', 'r');
$can_write = utility::havePrivilege('master_file', 'w');

if (!$can_read) {
    die('');
}


if (isset($_POST['saveData'])) {
    $collTypeName = trim(strip_tags($_POST['collTypeName']));
    
    if (empty($collTypeName)) {
        utility::jsToastr(__('Collection Type'),__('Collection type name can't be empty'),'error');
        exit();
    } else {
      

# TF-IDF processing and modeling all supervised not tuned

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 36000 entries, 0 to 35999
Data columns (total 3 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   code       36000 non-null  object
 1   vuln_type  36000 non-null  object
 2   cleaned    36000 non-null  object
dtypes: object(3)
memory usage: 843.9+ KB


In [ ]:
dfin = df.drop(['code'], axis=1)

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split

X_tif = dfin.drop(['vuln_type'], axis=1)
y_tif = dfin['vuln_type']
X_train_tif, X_test_tif, y_train_tif, y_test_tif = train_test_split(X_tif, y_tif, test_size=0.2, random_state=45)

vectorizer_tf = TfidfVectorizer(lowercase = False, ngram_range=(2,7), token_pattern = '[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+', stop_words=[';'], binary=True)

#vecto_tf = vectorizer_tf
vecto_tf = vectorizer_tf.fit(X_train_tif['cleaned'])
X_train_vec_tf = vecto_tf.transform(X_train_tif['cleaned'])
X_test_vec_tf = vecto_tf.transform(X_test_tif['cleaned'])

In [ ]:
feat_name = []
feat_count = []
for x in vecto_tf.vocabulary_:
  print("[+] Feature: " + f"'{str(x)}'")
  feat_name.append(str(x))
  print("[+] Value: " + str(vecto_tf.vocabulary_[x]))
  feat_count.append(vecto_tf.vocabulary_[x])
  print("\n")

type(vecto_tf.vocabulary_)

[+] Feature: '<?php $tainted'
[+] Value: 8649


[+] Feature: '$tainted ='
[+] Value: 2591


[+] Feature: '= filter_input(INPUT_GET,'
[+] Value: 10122


[+] Feature: 'filter_input(INPUT_GET, t'
[+] Value: 17622


[+] Feature: 't ,'
[+] Value: 21991


[+] Feature: ', FILTER_SANITIZE_FULL_SPECIAL_CHARS);'
[+] Value: 5909


[+] Feature: 'FILTER_SANITIZE_FULL_SPECIAL_CHARS); if(gettype($tainted)'
[+] Value: 13022


[+] Feature: 'if(gettype($tainted) =='
[+] Value: 19426


[+] Feature: '== string'
[+] Value: 11352


[+] Feature: 'string )'
[+] Value: 21537


[+] Feature: ') {'
[+] Value: 4405


[+] Feature: '{ $sanitized'
[+] Value: 24280


[+] Feature: '$sanitized ='
[+] Value: 1894


[+] Feature: '= $tainted;'
[+] Value: 9499


[+] Feature: '$tainted; $dataflow'
[+] Value: 3418


[+] Feature: '$dataflow ='
[+] Value: 829


[+] Feature: '= $sanitized;'
[+] Value: 9162


[+] Feature: '$sanitized; $context'
[+] Value: 2395


[+] Feature: '$context ='
[+] Value: 607


[+] Feature: '= (('
[+] V

dict

## Supervised not tuned using tf-idf

### Gaussian naive bayes

In [ ]:
from sklearn.naive_bayes import GaussianNB
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from yellowbrick.classifier import ClassificationReport
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
GNB_vec_tf_idf = GaussianNB()
GNB_vec_tf_idf.fit(X_train_vec_tf.toarray(), y_train_tif)
print('--------------------- GaussianNB ( CODE ) ----------------------------')

y_pred = GNB_vec_tf_idf.predict(X_test_vec_tf.toarray())

print(classification_report(y_test_tif, y_pred))
print('--------------------- confusion matrix  ----------------------------')
print(confusion_matrix(y_test_tif, y_pred))

y_true = y_test_tif
dt_pred = GNB_vec_tf_idf.predict(X_test_vec_tf.toarray())
matrix = confusion_matrix(y_true, dt_pred)
print('-------------- TN FN TP FP --------------')
label_names = pd.Series(['XSS', 'SQL', 'Secure'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

--------------------- GaussianNB ( CODE ) ----------------------------
                          precision    recall  f1-score   support

          Not Vulnerable       1.00      0.89      0.94      2429
SQL Injection Vulnerable       0.94      1.00      0.97      2375
          XSS Vulnerable       0.96      1.00      0.98      2396

                accuracy                           0.96      7200
               macro avg       0.96      0.96      0.96      7200
            weighted avg       0.96      0.96      0.96      7200

--------------------- confusion matrix  ----------------------------
[[2158  164  107]
 [   4 2371    0]
 [   1    0 2395]]
-------------- TN FN TP FP --------------


Predicted XSS  Predicted SQL  Predicted Secure
Is XSS              2158            164               107
Is SQL                 4           2371                 0
Is Secure              1              0              2395

### Multinomial naive bayes

In [ ]:
from sklearn.naive_bayes import MultinomialNB
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from yellowbrick.classifier import ClassificationReport
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
MNB_vec_tf_idf = MultinomialNB()
MNB_vec_tf_idf.fit(X_train_vec_tf.toarray(), y_train_tif)
print('--------------------- MultinomialNB ( CODE ) ----------------------------')

y_pred = MNB_vec_tf_idf.predict(X_test_vec_tf.toarray())

print(classification_report(y_test_tif, y_pred))
print('--------------------- confusion matrix  ----------------------------')
print(confusion_matrix(y_test_tif, y_pred))

y_true = y_test_tif
dt_pred = MNB_vec_tf_idf.predict(X_test_vec_tf.toarray())
matrix = confusion_matrix(y_true, dt_pred)
print('-------------- TN FN TP FP --------------')
label_names = pd.Series(['XSS', 'SQL', 'Secure'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

--------------------- MultinomialNB ( CODE ) ----------------------------
                          precision    recall  f1-score   support

          Not Vulnerable       1.00      0.68      0.81      2429
SQL Injection Vulnerable       0.84      1.00      0.91      2375
          XSS Vulnerable       0.88      1.00      0.94      2396

                accuracy                           0.89      7200
               macro avg       0.91      0.89      0.89      7200
            weighted avg       0.91      0.89      0.89      7200

--------------------- confusion matrix  ----------------------------
[[1658  447  324]
 [   0 2375    0]
 [   0    0 2396]]
-------------- TN FN TP FP --------------


Predicted XSS  Predicted SQL  Predicted Secure
Is XSS              1658            447               324
Is SQL                 0           2375                 0
Is Secure              0              0              2396

### Random Forest

In [ ]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from yellowbrick.classifier import ClassificationReport
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
RFC_vec_tf_idf = RandomForestClassifier()
RFC_vec_tf_idf.fit(X_train_vec_tf.toarray(), y_train_tif)
print('--------------------- RandomForestClassifier ( CODE ) ----------------------------')

y_pred = RFC_vec_tf_idf.predict(X_test_vec_tf.toarray())

print(classification_report(y_test_tif, y_pred))
print('--------------------- confusion matrix  ----------------------------')
print(confusion_matrix(y_test_tif, y_pred))

y_true = y_test_tif
dt_pred = RFC_vec_tf_idf.predict(X_test_vec_tf.toarray())
matrix = confusion_matrix(y_true, dt_pred)
print('-------------- TN FN TP FP --------------')
label_names = pd.Series(['XSS', 'SQL', 'Secure'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

--------------------- RandomForestClassifier ( CODE ) ----------------------------
                          precision    recall  f1-score   support

          Not Vulnerable       0.97      0.93      0.95      2429
SQL Injection Vulnerable       0.97      0.98      0.97      2375
          XSS Vulnerable       0.97      0.98      0.97      2396

                accuracy                           0.97      7200
               macro avg       0.97      0.97      0.97      7200
            weighted avg       0.97      0.97      0.97      7200

--------------------- confusion matrix  ----------------------------
[[2265   84   80]
 [  38 2337    0]
 [  42    0 2354]]
-------------- TN FN TP FP --------------


Predicted XSS  Predicted SQL  Predicted Secure
Is XSS              2265             84                80
Is SQL                38           2337                 0
Is Secure             42              0              2354

### Decision Tree

In [ ]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from yellowbrick.classifier import ClassificationReport
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
DTC_vec_tf_idf = DecisionTreeClassifier()
DTC_vec_tf_idf.fit(X_train_vec_tf.toarray(), y_train_tif)
print('--------------------- DecisionTreeClassifier ( CODE ) ----------------------------')

y_pred = DTC_vec_tf_idf.predict(X_test_vec_tf.toarray())

print(classification_report(y_test_tif, y_pred))
print('--------------------- confusion matrix  ----------------------------')
print(confusion_matrix(y_test_tif, y_pred))

y_true = y_test_tif
dt_pred = DTC_vec_tf_idf.predict(X_test_vec_tf.toarray())
matrix = confusion_matrix(y_true, dt_pred)
print('-------------- TN FN TP FP --------------')
label_names = pd.Series(['XSS', 'SQL', 'Secure'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

--------------------- DecisionTreeClassifier ( CODE ) ----------------------------
                          precision    recall  f1-score   support

          Not Vulnerable       0.94      0.93      0.94      2429
SQL Injection Vulnerable       0.97      0.98      0.97      2375
          XSS Vulnerable       0.96      0.97      0.96      2396

                accuracy                           0.96      7200
               macro avg       0.96      0.96      0.96      7200
            weighted avg       0.96      0.96      0.96      7200

--------------------- confusion matrix  ----------------------------
[[2259   83   87]
 [  53 2322    0]
 [  82    0 2314]]
-------------- TN FN TP FP --------------


Predicted XSS  Predicted SQL  Predicted Secure
Is XSS              2259             83                87
Is SQL                53           2322                 0
Is Secure             82              0              2314

### Linear svc

In [ ]:
from sklearn.svm import LinearSVC
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from yellowbrick.classifier import ClassificationReport
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif

from sklearn.calibration import CalibratedClassifierCV
lsvc = LinearSVC()
LSVC_vec_tf_idf = CalibratedClassifierCV(lsvc, cv=5)
LSVC_vec_tf_idf.fit(X_train_vec_tf.toarray(), y_train_tif)
print('--------------------- LinearSVC ( CODE ) ----------------------------')

y_pred = LSVC_vec_tf_idf.predict(X_test_vec_tf.toarray())

print(classification_report(y_test_tif, y_pred))
print('--------------------- confusion matrix  ----------------------------')
print(confusion_matrix(y_test_tif, y_pred))

y_true = y_test_tif
dt_pred = LSVC_vec_tf_idf.predict(X_test_vec_tf.toarray())
matrix = confusion_matrix(y_true, dt_pred)
print('-------------- TN FN TP FP --------------')
label_names = pd.Series(['XSS', 'SQL', 'Secure'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

--------------------- LinearSVC ( CODE ) ----------------------------
                          precision    recall  f1-score   support

          Not Vulnerable       0.99      0.96      0.98      2429
SQL Injection Vulnerable       0.98      1.00      0.99      2375
          XSS Vulnerable       0.98      1.00      0.99      2396

                accuracy                           0.98      7200
               macro avg       0.98      0.98      0.98      7200
            weighted avg       0.98      0.98      0.98      7200

--------------------- confusion matrix  ----------------------------
[[2333   42   54]
 [   7 2368    0]
 [   7    0 2389]]
-------------- TN FN TP FP --------------


Predicted XSS  Predicted SQL  Predicted Secure
Is XSS              2333             42                54
Is SQL                 7           2368                 0
Is Secure              7              0              2389

### Testing the models using all-supervised not tuned tf-idf

In [ ]:
def predict_code_no_feature(strig):
    data = process_php_tokenized(strig)
    X_testt = vecto_tf.transform([data])
    X_testt_dense = X_testt.toarray()  # buat GNB

    models = {
        "GaussianNB": GNB_vec_tf_idf,
        "MultinomialNB": MNB_vec_tf_idf,
        "DecisionTree": DTC_vec_tf_idf,
        "RandomForest": RFC_vec_tf_idf,
        "LinearSVC": LSVC_vec_tf_idf,
    }

    print("Vulnerability Detection with TF-IDF:")
    for name, model in models.items():
        try:
            # model dengan predict_proba
            probs = model.predict_proba(X_testt_dense if name=="GaussianNB" else X_testt)[0]
            classes = model.classes_
        except AttributeError:
            # fallback LinearSVC
            if hasattr(model, "decision_function"):
                scores = model.decision_function(X_testt)
                exp_scores = np.exp(scores - np.max(scores))
                probs = exp_scores / exp_scores.sum()
                classes = model.classes_
            else:
                pred = model.predict(X_testt)[0]
                classes = model.classes_
                probs = [1.0 if c == pred else 0.0 for c in classes]

        # cetak semua probabilitas tiap kelas
        print(f"🧪 {name} results:")
        for cls, prob in zip(classes, probs):
            prob_scalar = np.ravel(prob)[0]   # pastikan jadi 1 float
            print(f"   - {cls}: {prob_scalar*100:.2f}%")
        print()

In [ ]:
# CVE-2025-25403
test_code = """
<?php
/**
 * Copyright (C) 2007,2008  Arie Nugraha (dicarve@yahoo.com)
 *
 * This program is free software; you can redistribute it and/or modify
 * it under the terms of the GNU General Public License as published by
 * the Free Software Foundation; either version 3 of the License, or
 * (at your option) any later version.
 *
 * This program is distributed in the hope that it will be useful,
 * but WITHOUT ANY WARRANTY; without even the implied warranty of
 * MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
 * GNU General Public License for more details.
 *
 * You should have received a copy of the GNU General Public License
 * along with this program; if not, write to the Free Software
 * Foundation, Inc., 51 Franklin Street, Fifth Floor, Boston, MA  02110-1301  USA
 *
 */

/* Collection Type Management section */

// key to authenticate
define('INDEX_AUTH', '1');
// key to get full database access
define('DB_ACCESS', 'fa');

// main system configuration
require '../../../sysconfig.inc.php';
// IP based access limitation
require LIB.'ip_based_access.inc.php';
do_checkIP('smc');
do_checkIP('smc-masterfile');
// start the session
require SB.'admin/default/session.inc.php';
require SB.'admin/default/session_check.inc.php';
require SIMBIO.'simbio_GUI/table/simbio_table.inc.php';
require SIMBIO.'simbio_GUI/form_maker/simbio_form_table_AJAX.inc.php';
require SIMBIO.'simbio_GUI/paging/simbio_paging.inc.php';
require SIMBIO.'simbio_DB/datagrid/simbio_dbgrid.inc.php';
require SIMBIO.'simbio_DB/simbio_dbop.inc.php';

// privileges checking
$can_read = utility::havePrivilege('master_file', 'r');
$can_write = utility::havePrivilege('master_file', 'w');

if (!$can_read) {
    die('<div class="errorBox">'.__('You don\'t have enough privileges to view this section').'</div>');
}

/* RECORD OPERATION */
if (isset($_POST['saveData'])) {
    $collTypeName = trim(strip_tags($_POST['collTypeName']));
    // check form validity
    if (empty($collTypeName)) {
        utility::jsToastr(__('Collection Type'),__('Collection type name can\'t be empty'),'error');
        exit();
    } else {
        $data['coll_type_name'] = $dbs->escape_string($collTypeName);
        $data['input_date'] = date('Y-m-d');
        $data['last_update'] = date('Y-m-d');

        // create sql op object
        $sql_op = new simbio_dbop($dbs);
        if (isset($_POST['updateRecordID'])) {
            /* UPDATE RECORD MODE */
            // remove input date
            unset($data['input_date']);
            // filter update record ID
            $updateRecordID = (integer)$_POST['updateRecordID'];
            // update the data
            $update = $sql_op->update('mst_coll_type', $data, 'coll_type_id='.$updateRecordID);
            if ($update) {
                utility::jsToastr(__('Collection Type'),__('Colllection Type Data Successfully Updated'),'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(parent.jQuery.ajaxHistory[0].url);</script>';
            } else { utility::jsToastr(__('Collection Type'),__('Colllection Type Data FAILED to Updated. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error); }
            exit();
        } else {
            /* INSERT RECORD MODE */
            // insert the data
            $insert = $sql_op->insert('mst_coll_type', $data);
            if ($insert) {
                utility::jsToastr(__('Collection Type'),__('New Colllection Type Data Successfully Saved'),'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
            } else { utility::jsToastr(__('Collection Type'),__('Author Data FAILED to Save. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error,'error'); }
            exit();
        }
    }
    exit();
} else if (isset($_POST['itemID']) AND !empty($_POST['itemID']) AND isset($_POST['itemAction'])) {
    if (!($can_read AND $can_write)) {
        die();
    }
    /* DATA DELETION PROCESS */
    $sql_op = new simbio_dbop($dbs);
    $failed_array = array();
    $error_num = 0;
    if (!is_array($_POST['itemID'])) {
        // make an array
        $_POST['itemID'] = array((integer)$_POST['itemID']);
    }
    // loop array
    foreach ($_POST['itemID'] as $itemID) {
        $itemID = (integer)$itemID;
        // check if this item data still have an item
        $item_q = $dbs->query('SELECT ct.coll_type_name, COUNT(item_id) FROM item AS i
            LEFT JOIN mst_coll_type AS ct ON i.coll_type_id=ct.coll_type_id
            WHERE i.coll_type_id='.$itemID.' GROUP BY i.coll_type_id');
        $item_d = $item_q->fetch_row();
        if ($item_d[1] < 1) {
            if (!$sql_op->delete('mst_coll_type', "coll_type_id=$itemID")) {
                $error_num++;
            }
        } else {
            $still_have_item[] = sprintf(__('Collection type %s still used by %s items'),$item_d[0],$item_d[1]);
            $error_num++;
        }
    }

    if ($still_have_item) {
        $undeleted_coll_types = '';
        foreach ($still_have_item as $coll_type) {
            $undeleted_coll_types .= $coll_type."\n";
        }
        utility::jsToastr(__('Collection Type'),__('Below data can not be deleted:').$undeleted_coll_types,'error');
        exit();
    }
    // error alerting
    if ($error_num == 0) {
        utility::jsToastr(__('Collection Type'),__('All Data Successfully Deleted'),'success');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    } else {
        utility::jsToastr(__('Collection Type'),__('Some or All Data NOT deleted successfully!\nPlease contact system administrator'),'warning');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    }
    exit();
}
/* RECORD OPERATION END */

/* search form */
?>
<div class="menuBox">
<div class="menuBoxInner masterFileIcon">
	<div class="per_title">
	    <h2><?php echo __('Collection Type'); ?></h2>
  </div>
	<div class="sub_section">
	  <div class="btn-group">
      <a href="<?php echo MWB; ?>master_file/coll_type.php" class="btn btn-default"><?php echo __('Collection Type List'); ?></a>
      <a href="<?php echo MWB; ?>master_file/coll_type.php?action=detail" class="btn btn-default"><?php echo __('Add New Collection Type'); ?></a>
	  </div>
    <form name="search" action="<?php echo MWB; ?>master_file/coll_type.php" id="search" method="get" class="form-inline"><?php echo __('Search'); ?>
    <input type="text" name="keywords" class="form-control col-md-3" />
    <input type="submit" id="doSearch" value="<?php echo __('Search'); ?>" class="s-btn btn btn-default" />
    </form>
  </div>
</div>
</div>
<?php
/* search form end */
/* main content */
if (isset($_POST['detail']) OR (isset($_GET['action']) AND $_GET['action'] == 'detail')) {
    if (!($can_read AND $can_write)) {
        die('<div class="errorBox">'.__('You don\'t have enough privileges to view this section').'</div>');
    }
    $itemID = (integer)isset($_POST['itemID'])?$_POST['itemID']:0;
    $rec_q = $dbs->query("SELECT * FROM mst_coll_type WHERE coll_type_id=$itemID");
    $rec_d = $rec_q->fetch_assoc();

    // create new instance
    $form = new simbio_form_table_AJAX('mainForm', $_SERVER['PHP_SELF'].'?'.$_SERVER['QUERY_STRING'], 'post');
    $form->submit_button_attr = 'name="saveData" value="'.__('Save').'" class="s-btn btn btn-default"';

    // form table attributes
    $form->table_attr = 'id="dataList" class="s-table table"';
    $form->table_header_attr = 'class="alterCell font-weight-bold"';
    $form->table_content_attr = 'class="alterCell2"';

    // edit mode flag set
    if ($rec_q->num_rows > 0) {
        $form->edit_mode = true;
        // record ID for delete process
        $form->record_id = $itemID;
        // form record title
        $form->record_title = $rec_d['coll_type_name'];
        // submit button attribute
        $form->submit_button_attr = 'name="saveData" value="'.__('Update').'" class="s-btn btn btn-primary"';
    }

    /* Form Element(s) */
    // coll_type_name
    $form->addTextField('text', 'collTypeName', __('Collection Type').'*', $rec_d['coll_type_name']??'', 'style="width: 60%;" class="form-control"');

    // edit mode messagge
    if ($form->edit_mode) {
        echo '<div class="infoBox">'.__('You are going to edit collection type data').' : <b>'.$rec_d['coll_type_name'].'</b>  <br />'.__('Last Update').' '.$rec_d['last_update'].'</div>'; //mfc
    }
    // print out the form object
    echo $form->printOut();
} else {
    /* COLLECTION TYPE LIST */
    // table spec
    $table_spec = 'mst_coll_type AS ct';

    // create datagrid
    $datagrid = new simbio_datagrid();
    if ($can_read AND $can_write) {
        $datagrid->setSQLColumn('ct.coll_type_id', 'ct.coll_type_name AS \''.__('Collection Type').'\'', 'ct.last_update AS \''.__('Last Update').'\'');
    } else {
        $datagrid->setSQLColumn('ct.coll_type_name AS \''.__('Collection Type').'\'', 'ct.last_update AS \''.__('Last Update').'\'');
    }
    $datagrid->setSQLorder('coll_type_name ASC');

    // change the record order
    if (isset($_GET['fld']) AND isset($_GET['dir'])) {
        $datagrid->setSQLorder("'".urldecode($_GET['fld'])."' ".$dbs->escape_string($_GET['dir']));
    }

    // is there any search
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
       $keywords = utility::filterData('keywords', 'get', true, true, true);
       $datagrid->setSQLCriteria("ct.coll_type_name LIKE '%$keywords%'");
    }

    // set table and table header attributes
    $datagrid->table_attr = 'id="dataList" class="s-table table"';
    $datagrid->table_header_attr = 'class="dataListHeader" style="font-weight: bold;"';
    // set delete proccess URL
    $datagrid->chbox_form_URL = $_SERVER['PHP_SELF'];

    // put the result into variables
    $datagrid_result = $datagrid->createDataGrid($dbs, $table_spec, 20, ($can_read AND $can_write));
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
        $msg = str_replace('{result->num_rows}', $datagrid->num_rows, __('Found <strong>{result->num_rows}</strong> from your keywords')); //mfc
        echo '<div class="infoBox">'.$msg.' : "'.htmlspecialchars($_GET['keywords']).'"</div>';
    }

    echo $datagrid_result;
}
/* main content end */

"""
predict_code_no_feature(test_code)

Vulnerability Detection with TF-IDF:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 0.01%
   - SQL Injection Vulnerable: 0.00%
   - XSS Vulnerable: 99.99%

🧪 DecisionTree results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 1.00%
   - SQL Injection Vulnerable: 99.00%
   - XSS Vulnerable: 0.00%

🧪 LinearSVC results:
   - Not Vulnerable: 41.56%
   - SQL Injection Vulnerable: 58.30%
   - XSS Vulnerable: 0.14%



In [ ]:
# CVE-2025-45818
test_code = """
<?php
/**
 * Copyright (C) 2009  Arie Nugraha (dicarve@yahoo.com)
 *
 * This program is free software; you can redistribute it and/or modify
 * it under the terms of the GNU General Public License as published by
 * the Free Software Foundation; either version 3 of the License, or
 * (at your option) any later version.
 *
 * This program is distributed in the hope that it will be useful,
 * but WITHOUT ANY WARRANTY; without even the implied warranty of
 * MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
 * GNU General Public License for more details.
 *
 * You should have received a copy of the GNU General Public License
 * along with this program; if not, write to the Free Software
 * Foundation, Inc., 51 Franklin Street, Fifth Floor, Boston, MA  02110-1301  USA
 *
 */

/* Item Status Management section */

// key to authenticate
define('INDEX_AUTH', '1');
// key to get full database access
define('DB_ACCESS', 'fa');

// main system configuration
require '../../../sysconfig.inc.php';
// IP based access limitation
require LIB.'ip_based_access.inc.php';
do_checkIP('smc');
do_checkIP('smc-masterfile');
// start the session
require SB.'admin/default/session.inc.php';
require SB.'admin/default/session_check.inc.php';
require SIMBIO.'simbio_GUI/table/simbio_table.inc.php';
require SIMBIO.'simbio_GUI/form_maker/simbio_form_table_AJAX.inc.php';
require SIMBIO.'simbio_GUI/paging/simbio_paging.inc.php';
require SIMBIO.'simbio_DB/datagrid/simbio_dbgrid.inc.php';
require SIMBIO.'simbio_DB/simbio_dbop.inc.php';

// privileges checking
$can_read = utility::havePrivilege('master_file', 'r');
$can_write = utility::havePrivilege('master_file', 'w');

if (!$can_read) {
    die('<div class="errorBox">'.__('You don\'t have enough privileges to access this area!').'</div>');
}

// item status rules
$rules_option[] = array(NO_LOAN_TRANSACTION, __('No Loan Transaction'));
$rules_option[] = array(SKIP_STOCK_TAKE, __('Skipped By Stock Take'));

/* RECORD OPERATION */
if (isset($_POST['saveData'])) {
    $itemStatusID = strip_tags(trim($_POST['itemStatusID']));
    $itemStatusName = strip_tags(trim($_POST['itemStatus']));
    // check form validity
    if (empty($itemStatusID) OR empty($itemStatusName)) {
        utility::jsToastr(__('Item Status'),__('Item Status ID and Name can\'t be empty'),'error');
        exit();
    } else {
        $data['item_status_id'] = $dbs->escape_string($itemStatusID);
        $data['item_status_name'] = $dbs->escape_string($itemStatusName);
        // parsing rules
		/*
        $rules = '';
        if (isset($_POST['rules']) AND !empty($_POST['rules'])) {
            $rules = serialize($_POST['rules']);
        } else {
            $rules = 'literal{NULL}';
        }
		*/
        $data['rules'] = 'literal{NULL}';
        $data['no_loan'] = '0';
        $data['skip_stock_take'] = '0';
        foreach ($_POST['rules']??[] as $rule) {
            if ((integer)$rule === NO_LOAN_TRANSACTION) $data['no_loan'] = '1';
            if ((integer)$rule === SKIP_STOCK_TAKE) $data['skip_stock_take'] = '1';
        }
        $data['input_date'] = date('Y-m-d');
        $data['last_update'] = date('Y-m-d');

        // create sql op object
        $sql_op = new simbio_dbop($dbs);
        if (isset($_POST['updateRecordID'])) {
            /* UPDATE RECORD MODE */
            // remove input date
            unset($data['input_date']);
            // filter update record ID
            $updateRecordID = $dbs->escape_string(trim($_POST['updateRecordID']));
            // update the data
            $update = $sql_op->update('mst_item_status', $data, 'item_status_id=\''.$updateRecordID.'\'');
            if ($update) {
                utility::jsToastr(__('Item Status'), __('New Item Status Data Successfully Updated'), 'success');
                // update item status ID in item table to keep data integrity
                $sql_op->update('item', array('item_status_id' => $data['item_status_id']), 'item_status_id=\''.$updateRecordID.'\'');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(parent.jQuery.ajaxHistory[0].url);</script>';
            } else {
                utility::jsToastr(__('Item Status'),__('Item Status Data FAILED to Updated. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error,'error');
            }
            exit();
        } else {
            /* INSERT RECORD MODE */
            // insert the data
            $insert = $sql_op->insert('mst_item_status', $data);
            if ($insert) {
                utility::jsToastr(__('Item Status'), __('New Item Status Data Successfully Saved'), 'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
            } else {
                utility::jsToastr(__('Item Status'), __('Item Status Data FAILED to Save. Please Contact System Administrator')."\n".$sql_op->error, 'error');
            }
            exit();
        }
    }
    exit();
} else if (isset($_POST['itemID']) AND !empty($_POST['itemID']) AND isset($_POST['itemAction'])) {
    if (!($can_read AND $can_write)) {
        die();
    }
    /* DATA DELETION PROCESS */
    $sql_op = new simbio_dbop($dbs);
    $failed_array = array();
    $error_num = 0;
    $still_have_item = array();
    if (!is_array($_POST['itemID'])) {
        // make an array
        $_POST['itemID'] = array($dbs->escape_string(trim($_POST['itemID'])));
    }
    // loop array
    foreach ($_POST['itemID'] as $itemID) {
        $itemID = $dbs->escape_string(trim($itemID));
        // check if this place data still in use items
        $_sql_status_item_q = sprintf('SELECT mis.item_status_name, COUNT(mis.item_status_id) FROM item AS i
        LEFT JOIN mst_item_status AS mis ON i.item_status_id=mis.item_status_id
        WHERE mis.item_status_id=%d GROUP BY mis.item_status_name', $itemID);
        $status_item_q = $dbs->query($_sql_status_item_q);
        $status_item_d = $status_item_q->fetch_row();
        if ($status_item_d[1] < 1) {
            if (!$sql_op->delete('mst_item_status', "item_status_id='$itemID'")) {
                $error_num++;
            }
        }else{
            $still_have_item[] = sprintf(__('%s still in use %d item ').'<br/>',substr($status_item_d[0], 0, 45),$status_item_d[1]);
            $error_num++;
        }
    }

    if ($still_have_item) {
        $titles = '';
        foreach ($still_have_item as $title) {
            $titles .= $title . "\n";
        }
        utility::jsToastr( __('Item Status'), __('Below data can not be deleted:') . "\n" . $titles, 'error');
        echo '<script type="text/javascript">parent.$(\'#mainContent\').simbioAJAX(\'' . $_SERVER['PHP_SELF'] . '\', {addData: \'' . $_POST['lastQueryStr'] . '\'});</script>';
        exit();
    }

    // error alerting
    if ($error_num == 0) {
        utility::jsToastr(__('Item Status'), __('All Data Successfully Deleted'), 'success');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    } else {
        utility::jsToastr(__('Item Status'), __('Some or All Data NOT deleted successfully!\nPlease contact system administrator'), 'warning');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    }
    exit();
}
/* item status update process end */

/* search form */
?>
<div class="menuBox">
<div class="menuBoxInner masterFileIcon">
	<div class="per_title">
	    <h2><?php echo __('Item Status'); ?></h2>
  </div>
	<div class="sub_section">
	  <div class="btn-group">
      <a href="<?php echo MWB; ?>master_file/item_status.php" class="btn btn-default"><?php echo __('Item Status'); ?></a>
		  <a href="<?php echo MWB; ?>master_file/item_status.php?action=detail" class="btn btn-default"><?php echo __('Add New Item Status'); ?></a>
	  </div>
    <form name="search" action="<?php echo MWB; ?>master_file/item_status.php" id="search" method="get" class="form-inline"><?php echo __('Search'); ?>
    <input type="text" name="keywords" class="form-control col-md-3" />
    <input type="submit" id="doSearch" value="<?php echo __('Search'); ?>" class="s-btn btn btn-default" />
    </form>
	</div>
</div>
</div>
<?php
/* search form end */
/* main content */
if (isset($_POST['detail']) OR (isset($_GET['action']) AND $_GET['action'] == 'detail')) {
    if (!($can_read AND $can_write)) {
        die('<div class="errorBox">'.__('You don\'t have enough privileges to access this area!').'</div>');
    }
    /* RECORD FORM */
    $itemID = trim($dbs->escape_string(isset($_POST['itemID'])?$_POST['itemID']:''));
    $rec_q = $dbs->query("SELECT * FROM mst_item_status WHERE item_status_id='$itemID'");
    $rec_d = $rec_q->fetch_assoc();

    // create new instance
    $form = new simbio_form_table_AJAX('mainForm', $_SERVER['PHP_SELF'].'?'.$_SERVER['QUERY_STRING'], 'post');
    $form->submit_button_attr = 'name="saveData" value="'.__('Save').'" class="s-btn btn btn-default"';

    // form table attributes
    $form->table_attr = 'id="dataList" class="s-table table"';
    $form->table_header_attr = 'class="alterCell font-weight-bold"';
    $form->table_content_attr = 'class="alterCell2"';

    // edit mode flag set
    if ($rec_q->num_rows > 0) {
        $form->edit_mode = true;
        // record ID for delete process
        $form->record_id = $itemID;
        // form record title
        $form->record_title = $rec_d['item_status_name'];
        // submit button attribute
        $form->submit_button_attr = 'name="saveData" value="'.__('Update').'" class="s-btn btn btn-primary"';
    }

    /* Form Element(s) */
    // item status code
    $form->addTextField('text', 'itemStatusID', __('Item Status Code').'*', $rec_d['item_status_id']??'', 'style="width: 20%;" maxlength="3" class="form-control"');
    // item status name
    $form->addTextField('text', 'itemStatus', __('Item Status Name').'*', $rec_d['item_status_name']??'', 'style="width: 60%;" class="form-control"');
    // item status rules
	$rules = array();

	if ($rec_d['no_loan']??false) $rules[] = NO_LOAN_TRANSACTION;

	if ($rec_d['skip_stock_take']??false) $rules[] = SKIP_STOCK_TAKE;

    $form->addCheckbox('rules', __('Rules'), $rules_option, $rules);

    // edit mode messagge
    if ($form->edit_mode) {
        echo '<div class="infoBox">'.__('You are going to edit Item Status data').' : <b>'.$rec_d['item_status_name'].'</b>  <br />'.__('Last Update').' '.$rec_d['last_update'].'</div>'; //mfc
    }
    // print out the form object
    echo $form->printOut();
} else {
    /* ITEM STATUS LIST */
    // table spec
    $table_spec = 'mst_item_status AS ist';

    // create datagrid
    $datagrid = new simbio_datagrid();
    if ($can_read AND $can_write) {
        $datagrid->setSQLColumn('ist.item_status_id',
            'ist.item_status_id AS \''.__('Item Status Code').'\'',
            'ist.item_status_name AS \''.__('Item Status Name').'\'',
            'ist.last_update AS \''.__('Last Update').'\'');
    } else {
        $datagrid->setSQLColumn('ist.item_status_id AS \''.__('Item Status Code').'\'',
            'ist.item_status_name AS \''.__('Item Status Name').'\'',
            'ist.last_update AS \''.__('Last Update').'\'');
    }
    $datagrid->setSQLorder('item_status_name ASC');

    // change the record order
    if (isset($_GET['fld']) AND isset($_GET['dir'])) {
        $datagrid->setSQLorder("'".urldecode($_GET['fld'])."' ".$dbs->escape_string($_GET['dir']));
    }

    // is there any search
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
       $keywords = utility::filterData('keywords', 'get', true, true, true);
       $datagrid->setSQLCriteria("ist.item_status_name LIKE '%$keywords%'");
    }

    // set table and table header attributes
    $datagrid->table_attr = 'id="dataList" class="s-table table"';
    $datagrid->table_header_attr = 'class="dataListHeader" style="font-weight: bold;"';
    // set delete proccess URL
    $datagrid->chbox_form_URL = $_SERVER['PHP_SELF'];

    // put the result into variables
    $datagrid_result = $datagrid->createDataGrid($dbs, $table_spec, 20, ($can_read AND $can_write));
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
        $msg = str_replace('{result->num_rows}', $datagrid->num_rows, __('Found <strong>{result->num_rows}</strong> from your keywords')); //mfc
        echo '<div class="infoBox">'.$msg.' : "'.htmlspecialchars($_GET['keywords']).'"</div>';
    }

    echo $datagrid_result;
}
/* main content end */
"""

predict_code_no_feature(test_code)

Vulnerability Detection with TF-IDF:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 0.00%
   - XSS Vulnerable: 100.00%

🧪 DecisionTree results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 2.00%
   - SQL Injection Vulnerable: 96.00%
   - XSS Vulnerable: 2.00%

🧪 LinearSVC results:
   - Not Vulnerable: 45.63%
   - SQL Injection Vulnerable: 54.22%
   - XSS Vulnerable: 0.15%



In [ ]:
# CVE-2025-45819
test = """
<?php
/**
 * Copyright (C) 2007,2008  Arie Nugraha (dicarve@yahoo.com)
 *
 * This program is free software; you can redistribute it and/or modify
 * it under the terms of the GNU General Public License as published by
 * the Free Software Foundation; either version 3 of the License, or
 * (at your option) any later version.
 *
 * This program is distributed in the hope that it will be useful,
 * but WITHOUT ANY WARRANTY; without even the implied warranty of
 * MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
 * GNU General Public License for more details.
 *
 * You should have received a copy of the GNU General Public License
 * along with this program; if not, write to the Free Software
 * Foundation, Inc., 51 Franklin Street, Fifth Floor, Boston, MA  02110-1301  USA
 *
 */

/* Author Management section */

// key to authenticate
if (!defined('INDEX_AUTH')) {
  define('INDEX_AUTH', '1');
}
// key to get full database access
define('DB_ACCESS', 'fa');

// main system configuration
if (!defined('SB')) {
  require '../../../sysconfig.inc.php';
}

// IP based access limitation
require LIB.'ip_based_access.inc.php';
do_checkIP('smc');
do_checkIP('smc-masterfile');

// start the session
require SB.'admin/default/session.inc.php';
require SB.'admin/default/session_check.inc.php';
require SIMBIO.'simbio_GUI/table/simbio_table.inc.php';
require SIMBIO.'simbio_GUI/form_maker/simbio_form_table_AJAX.inc.php';
require SIMBIO.'simbio_GUI/paging/simbio_paging.inc.php';
require SIMBIO.'simbio_DB/datagrid/simbio_dbgrid.inc.php';
require SIMBIO.'simbio_DB/simbio_dbop.inc.php';

// privileges checking
$can_read = utility::havePrivilege('master_file', 'r');
$can_write = utility::havePrivilege('master_file', 'w');

if (!$can_read) {
    die('<div class="errorBox">'.__('You don\'t have enough privileges to access this area!').'</div>');
}

$in_pop_up = false;
// check if we are inside pop-up window
if (isset($_GET['inPopUp'])) {
  $in_pop_up = true;
}

/* RECORD OPERATION */
if (isset($_POST['saveData']) AND $can_read AND $can_write) {
    $authorName = trim(strip_tags($_POST['authorName']));
    // check form validity
    if (empty($authorName)) {
        utility::jsToastr(__('Author'),__('Author name can\'t be empty'),'warning');
        exit();
    } else {
        $data['author_name'] = $dbs->escape_string($authorName);
        $author_year = $dbs->escape_string(trim($_POST['authorYear']));
        if ($author_year) { $data['author_year'] = $author_year; }
        $data['authority_type'] = trim($dbs->escape_string(strip_tags($_POST['authorityType'])));
        $data['auth_list'] = trim($dbs->escape_string(strip_tags($_POST['authList'])));
        $data['input_date'] = date('Y-m-d');
        $data['last_update'] = date('Y-m-d');

        // create sql op object
        $sql_op = new simbio_dbop($dbs);
        if (isset($_POST['updateRecordID'])) {
            /* UPDATE RECORD MODE */
            // remove input date
            unset($data['input_date']);
            // filter update record ID
            $updateRecordID = (integer)$_POST['updateRecordID'];
            // update the data
            $update = $sql_op->update('mst_author', $data, 'author_id='.$updateRecordID);
            if ($update) {
                utility::writeLogs($dbs, 'staff', $_SESSION['uid'], 'Master file', $_SESSION['realname'].' update author ('.$data['author_name'].').', 'Author', 'update');
                utility::jsToastr(__('Author'),__('Author Data Successfully Updated'),'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(parent.jQuery.ajaxHistory[0].url);</script>';
                if ($in_pop_up) {
                    echo '<script type="text/javascript">top.setIframeContent(\'authorIframe\', \''.MWB.'bibliography/iframe_author.php?biblioID='.$_GET['biblio_id'].'\');</script>';
                    echo '<script type="text/javascript">top.jQuery.colorbox.close();</script>';
                } else {
                    echo '<script type="text/javascript">parent.$(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
                }
            } else { utility::jsToastr(__('Author'),__('Author Data FAILED to Updated. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error,'error'); }
            exit();
        } else {
            /* INSERT RECORD MODE */
            // insert the data
            $insert = $sql_op->insert('mst_author', $data);
            if ($insert) {
                utility::writeLogs($dbs, 'staff', $_SESSION['uid'], 'Master file', $_SESSION['realname'].' add new author ('.$data['author_name'].').', 'Author', 'Add');
                utility::jsToastr(__('Author'),__('New Author Data Successfully Saved'),'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
                if ($in_pop_up) {
                    echo '<script type="text/javascript">top.setIframeContent(\'authorIframe\', \''.MWB.'bibliography/iframe_author.php?biblioID='.$_GET['biblio_id'].'\');</script>';
                    echo '<script type="text/javascript">top.jQuery.colorbox.close();</script>';
                } else {
                    echo '<script type="text/javascript">parent.$(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
                }

            } else {
                utility::writeLogs($dbs, 'staff', $_SESSION['uid'], 'Master file', $_SESSION['realname'].' can not add new author ('.$data['author_name'].').', 'Author', 'Fail');
                utility::jsToastr(__('Author'),__('Author Data FAILED to Save. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error,'error');
            }
            exit();
        }
    }
    exit();
} else if (isset($_POST['itemID']) AND !empty($_POST['itemID']) AND isset($_POST['itemAction'])) {
    if (!($can_read AND $can_write)) {
        die();
    }
    /* DATA DELETION PROCESS */
    $sql_op = new simbio_dbop($dbs);
    $failed_array = array();
    $error_num = 0;
    $still_used_biblio = array();
    if (!is_array($_POST['itemID'])) {
        // make an array
        $_POST['itemID'] = array((integer)$_POST['itemID']);
    }
    // loop array
    foreach ($_POST['itemID'] as $itemID) {
        $itemID = (integer)$itemID;

        // check if this author data still used biblio
        $_sql_biblio_author_q = sprintf('SELECT  ma.author_name, COUNT(ma.author_id),b.title FROM biblio AS b
        LEFT JOIN biblio_author ba ON ba.biblio_id=b.biblio_id
        LEFT JOIN mst_author ma ON ma.author_id=ba.author_id
        WHERE ma.author_id=%d GROUP BY b.title', $itemID);
        $biblio_author_q = $dbs->query($_sql_biblio_author_q);
        $biblio_author_d = $biblio_author_q->fetch_row();
        $_log_authors .= $biblio_author_d['author_name'].', ';

        if ($biblio_author_d[1] < 1) {
            if (!$sql_op->delete('mst_author', 'author_id='.$itemID)) {
                $error_num++;
            }
        }
         else {
            $still_used_biblio[] = substr($biblio_author_d[0], 0, 6).'... still used biblio '.substr($biblio_author_d[2], 0, 6).' ..'."\n";
            $error_num++;
        }
    }

    if ($still_used_biblio) {
        $titles = '';
        foreach ($still_used_biblio as $title) {
          $titles .= $title."\n";
        }
        utility::jsToastr(__('Author'),__('Below data can not be deleted:')."\n".$titles, 'warning');
        echo '<script type="text/javascript">parent.$(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\', {addData: \''.$_POST['lastQueryStr'].'\'});</script>';
        exit();
    }

    // error alerting
    if ($error_num == 0) {
        utility::writeLogs($dbs, 'staff', $_SESSION['uid'], 'Master file', $_SESSION['realname'].' delete  author ('.implode(', ', $_log_authors).').', 'Author', 'delete');
        utility::jsToastr(__('Author'),__('All Data Successfully Deleted'),'success');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    } else {
        utility::writeLogs($dbs, 'staff', $_SESSION['uid'], 'Master file', $_SESSION['realname'].' delete  author(s), BUT not all ('.implode(', ', $_log_authors).').', 'Author', 'delete');
        utility::jsToastr(__('Author'),__('Some or All Data NOT deleted successfully!\nPlease contact system administrator'),'error');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    }
    exit();
}
/* RECORD OPERATION END */

/* search form */
if (!$in_pop_up) {
?>
<div class="menuBox">
<div class="menuBoxInner masterFileIcon">
	<div class="per_title">
	    <h2><?php echo __('Author'); ?></h2>
  </div>
	<div class="sub_section">
	  <div class="btn-group">
      <a href="<?php echo MWB; ?>master_file/author.php" class="btn btn-default"><?php echo __('Author List'); ?></a>
      <a href="<?php echo MWB; ?>master_file/author.php?action=detail" class="btn btn-default"><?php echo __('Add New Author'); ?></a>
    </div>
    <form name="search" action="<?php echo MWB; ?>master_file/author.php" id="search" method="get" class="form-inline"><?php echo __('Search'); ?>
    <input type="text" name="keywords" class="form-control col-md-3" />
    <input type="submit" id="doSearch" value="<?php echo __('Search'); ?>" class="s-btn btn btn-default" />
    </form>
  </div>
</div>
</div>
<?php
}

/* search form end */
/* main content */
if (isset($_POST['detail']) OR (isset($_GET['action']) AND $_GET['action'] == 'detail')) {
    if (!($can_read AND $can_write)) {
        die('<div class="errorBox">'.__('You don\'t have enough privileges to access this area!').'</div>');
    }
    /* RECORD FORM */
    $itemID = (integer)isset($_POST['itemID'])?$_POST['itemID']:0;
    $rec_q = $dbs->query('SELECT * FROM mst_author WHERE author_id='.$itemID);
    $rec_d = $rec_q->fetch_assoc();

    // create new instance
    $form = new simbio_form_table_AJAX('authorForm', $_SERVER['PHP_SELF'].'?'.$_SERVER['QUERY_STRING'], 'post');
    $form->submit_button_attr = 'name="saveData" value="'.__('Save').'" class="s-btn btn btn-default"';

    // form table attributes
    $form->table_attr = 'id="dataList" class="s-table table"';
    $form->table_header_attr = 'class="alterCell font-weight-bold"';
    $form->table_content_attr = 'class="alterCell2"';

    // edit mode flag set
    if ($rec_q->num_rows > 0) {
        $form->edit_mode = true;
        // record ID for delete process
        if (!$in_pop_up) {
            $form->record_id = $itemID;
        } else {
            $form->addHidden('updateRecordID', $itemID);
            $form->back_button = false;
            $form->delete_button = false;
        }
        // form record title
        $form->record_title = $rec_d['author_name'];
        // submit button attribute
        $form->submit_button_attr = 'name="saveData" value="'.__('Update').'" class="s-btn btn btn-primary"';
    }

    /* Form Element(s) */
    // author name
    $form->addTextField('text', 'authorName', __('Author Name').'*', $rec_d['author_name']??'', ' class="form-control col-6"');
    // author year
    $form->addTextField('text', 'authorYear', __('Author Birth Year'), $rec_d['author_year']??'', ' class="form-control col-6"');
    // authority type
    foreach ($sysconf['authority_type'] as $auth_type_id => $auth_type) {
        $auth_type_options[] = array($auth_type_id, $auth_type);
    }
    $form->addSelectList('authorityType', __('Authority Type'), $auth_type_options, $rec_d['authority_type']??'',' class="form-control col-6"');
    // authority list
    $form->addTextField('text', 'authList', __('Authority Files'), $rec_d['auth_list']??'', ' class="form-control col-6"');

    // edit mode messagge
    if ($form->edit_mode) {
        echo '<div class="infoBox">'.__('You are going to edit author data').' : <b>'.$rec_d['author_name'].'</b> <br />'.__('Last Update').' '.$rec_d['last_update'].'</div>'; //mfc
    }
    // print out the form object
    echo $form->printOut();
} else {
    /* AUTHOR LIST */
    // table spec
    $sql_criteria = 'a.author_id > 0';
    if (isset($_GET['type']) && $_GET['type'] == 'orphaned') {
        $table_spec = 'mst_author AS a LEFT JOIN biblio_author AS ba ON a.author_id=ba.author_id';
        $sql_criteria = 'ba.biblio_id IS NULL OR ba.author_id IS NULL';
    } else {
        $table_spec = 'mst_author AS a';
    }


    // authority field num
    $auth_type_fld = 2;
    // create datagrid
    $datagrid = new simbio_datagrid();
    if ($can_read AND $can_write) {
        $auth_type_fld = 3;
        $datagrid->setSQLColumn('a.author_id', 'a.author_name AS \''.__('Author Name').'\'',
            'a.author_year AS \''.__('Author Year').'\'',
            'a.authority_type AS \''.__('Authority Type').'\'',
            'a.auth_list AS \''.__('Authority Files').'\'',
            'a.last_update AS \''.__('Last Update').'\'');
    } else {
        $datagrid->setSQLColumn('a.author_name AS \''.__('Author Name').'\'',
            'a.author_year AS \''.__('Author Year').'\'',
            'a.authority_type AS \''.__('Authority Type').'\'',
            'a.auth_list AS \''.__('Authority Files').'\'',
            'a.last_update AS \''.__('Last Update').'\'');
    }
    $datagrid->setSQLorder('author_name ASC');

    // change the record order
    if (isset($_GET['fld']) AND isset($_GET['dir'])) {
        $datagrid->setSQLorder("'".urldecode($_GET['fld'])."' ".$dbs->escape_string($_GET['dir']));
    }

    // is there any search
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
       $keywords = utility::filterData('keywords', 'get', true, true, true);
       $sql_criteria .= " AND a.author_name LIKE '%$keywords%'";
    }
    $datagrid->setSQLCriteria($sql_criteria);

    // set table and table header attributes
    $datagrid->table_attr = 'id="dataList" class="s-table table"';
    $datagrid->table_header_attr = 'class="dataListHeader" style="font-weight: bold;"';
    // set delete proccess URL
    $datagrid->chbox_form_URL = $_SERVER['PHP_SELF'];

    // callback function to change value of authority type
    function callbackAuthorType($obj_db, $rec_d)
    {
        global $sysconf, $auth_type_fld;
        return $sysconf['authority_type'][$rec_d[$auth_type_fld]];
    }
    // modify column content
    $datagrid->modifyColumnContent($auth_type_fld, 'callback{callbackAuthorType}');
    // put the result into variable
    $datagrid_result = $datagrid->createDataGrid($dbs, $table_spec, 20, ($can_read AND $can_write));
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
        $msg = str_replace('{result->num_rows}', $datagrid->num_rows, __('Found <strong>{result->num_rows}</strong> from your keywords')); //mfc
        echo '<div class="infoBox">'.$msg.' : "'.htmlspecialchars($_GET['keywords']).'"</div>';
    }

    echo $datagrid_result;
}
/* main content end */
"""

predict_code_no_feature(test)

Vulnerability Detection with TF-IDF:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 0.00%
   - XSS Vulnerable: 100.00%

🧪 DecisionTree results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 1.00%
   - SQL Injection Vulnerable: 97.00%
   - XSS Vulnerable: 2.00%

🧪 LinearSVC results:
   - Not Vulnerable: 57.98%
   - SQL Injection Vulnerable: 41.87%
   - XSS Vulnerable: 0.15%



In [ ]:
#CVE-2025-45820
test = """
<?php
/**
 * Copyright (C) 2007,2008  Arie Nugraha (dicarve@yahoo.com)
 *
 * This program is free software; you can redistribute it and/or modify
 * it under the terms of the GNU General Public License as published by
 * the Free Software Foundation; either version 3 of the License, or
 * (at your option) any later version.
 *
 * This program is distributed in the hope that it will be useful,
 * but WITHOUT ANY WARRANTY; without even the implied warranty of
 * MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
 * GNU General Public License for more details.
 *
 * You should have received a copy of the GNU General Public License
 * along with this program; if not, write to the Free Software
 * Foundation, Inc., 51 Franklin Street, Fifth Floor, Boston, MA  02110-1301  USA
 *
 */

/* Biblio Author */

// key to authenticate
if (!defined('INDEX_AUTH')) {
  define('INDEX_AUTH', '1');
}

// main system configuration
if (!defined('SB')) {
  require '../../../sysconfig.inc.php';
}

if (isset($_GET['authorID'])) {
  $_POST['itemID'] = $_GET['authorID'];
  $_POST['detail'] = true;
}

$_GET['inPopUp'] = true;

if(isset($_POST['updateData'])){
	$biblio_id = (integer)$_POST['biblio_id'];
	$author_id = (integer)$_POST['author_id'];
	$level = (integer)$_POST['level'];
	$query = sprintf("UPDATE biblio_author SET level=%d WHERE biblio_id=%d AND author_id=%d",$level,$biblio_id,$author_id);
	$update = $dbs->query($query);
    if($update){
		utility::jsAlert('Authority Level Data Successfully Updated');
		echo '<script type="text/javascript">top.setIframeContent(\'authorIframe\', \''.MWB.'bibliography/iframe_author.php?biblioID='.$biblio_id.'\');</script>';
    	echo '<script type="text/javascript">top.jQuery.colorbox.close();</script>';
    }else {
    	utility::jsAlert( __('Authority Level Data FAILED to Updated. Please Contact System Administrator')."\nDEBUG : ".$update->error.$query);
		echo '<script type="text/javascript">top.setIframeContent(\'authorIframe\', \''.MWB.'bibliography/iframe_author.php?biblioID='.$_POST['biblioID'].'\');</script>';
    	echo '<script type="text/javascript">top.jQuery.colorbox.close();</script>';
    }
}

ob_start();

if(!isset($_GET['authority_level'])){
	require MDLBS.'master_file/author.php';
}
else{
	require SB.'admin/default/session.inc.php';
	require SB.'admin/default/session_check.inc.php';
	require SIMBIO.'simbio_GUI/table/simbio_table.inc.php';
	require SIMBIO.'simbio_GUI/form_maker/simbio_form_table_AJAX.inc.php';
	require SIMBIO.'simbio_GUI/paging/simbio_paging.inc.php';
	require SIMBIO.'simbio_DB/datagrid/simbio_dbgrid.inc.php';

    /* RECORD FORM */
    $itemID = (integer)isset($_POST['itemID'])?$_POST['itemID']:0;
    $query = 'SELECT b.biblio_id,ba.author_id,b.title,ma.author_name,ma.authority_type,ba.* FROM biblio b LEFT JOIN biblio_author ba ON ba.biblio_id=ba.biblio_id
    LEFT JOIN mst_author ma ON ma.author_id=ba.author_id WHERE b.biblio_id='.$_GET['biblio_id'].' AND ma.author_id='.$_GET['authorID'];
    $rec_q = $dbs->query($query);
    $rec_d = $rec_q->fetch_assoc();

	$form = new simbio_form_table_AJAX('authorLevelForm', $_SERVER['PHP_SELF'], 'post');
	$form->submit_button_attr = 'name="updateData" value="'.__('Update').'" class="btn btn-default"';

	// form table attributes
	$form->table_attr = 'id="dataList" class="s-table table"';
	$form->table_header_attr = 'class="alterCell font-weight-bold"';
	$form->table_content_attr = 'class="alterCell2"';

    /* Form Element(s) */
    $form->addHidden('biblio_id',$rec_d['biblio_id']);
    $form->addHidden('author_id',$rec_d['author_id']);
    // biblio title
    $form->addAnything(__('Title'),  $rec_d['title']);
    // author name
    $form->addAnything(__('Author Name'),  $rec_d['author_name']);
    // authority type
    $form->addAnything(__('Authority Type'),  $sysconf['authority_type'][$rec_d['authority_type']]);
    // authority_level
    foreach ($sysconf['authority_level'] as $authority_level_id => $authority_level) {
        $authority_level_options[] = array($authority_level_id, $authority_level);
    }
    $form->addSelectList('level', __('Authority Level'), $authority_level_options, (integer)$rec_d['level'],'class="form-control col-8"');
    // print out the form object
    echo $form->printOut();
}

$content = ob_get_clean();
// page title
$page_title = 'Biblio Author';

// include the page template
require SB.'/admin/'.$sysconf['admin_template']['dir'].'/notemplate_page_tpl.php';
"""

predict_code_no_feature(test)

Vulnerability Detection with TF-IDF:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 0.00%
   - XSS Vulnerable: 100.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 33.23%
   - SQL Injection Vulnerable: 33.42%
   - XSS Vulnerable: 33.35%

🧪 DecisionTree results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 8.00%
   - SQL Injection Vulnerable: 88.00%
   - XSS Vulnerable: 4.00%

🧪 LinearSVC results:
   - Not Vulnerable: 99.93%
   - SQL Injection Vulnerable: 0.00%
   - XSS Vulnerable: 0.07%



In [ ]:
test_dummy = """
<?php

$tainted = "a" + $_GET['p'];
echo $tainted;

?>
"""

predict_code_no_feature(test_dummy)

Vulnerability Detection with TF-IDF:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 0.00%
   - XSS Vulnerable: 100.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 17.27%
   - SQL Injection Vulnerable: 0.02%
   - XSS Vulnerable: 82.71%

🧪 DecisionTree results:
   - Not Vulnerable: 100.00%
   - SQL Injection Vulnerable: 0.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 30.00%
   - SQL Injection Vulnerable: 57.00%
   - XSS Vulnerable: 13.00%

🧪 LinearSVC results:
   - Not Vulnerable: 84.27%
   - SQL Injection Vulnerable: 0.00%
   - XSS Vulnerable: 15.73%



# TF-IDF Processing with hyperparam tuning algorithm

### random forest tuned

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer

# Tuning RandomForest
from sklearn.ensemble import RandomForestClassifier

pipeline = Pipeline([
    ('vect', TfidfVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';']
    )),
    ('clf', RandomForestClassifier(random_state=45, n_jobs=-1))
])

param_grid = {
    # TF-IDF parameters
    'vect__ngram_range': [(2,5), (2,7), (1,7)],
    'vect__max_df': [0.75, 1.0],
    'vect__binary': [True, False],
    # RandomForest parameters
    'clf__n_estimators': [100, 200],
    'clf__max_depth': [None, 20, 50],
    'clf__max_features': ['sqrt', 'log2'],
}

rf_grid = GridSearchCV(
    pipeline, param_grid,
    cv=3,
    scoring='f1_weighted',
    n_jobs=-1,
    verbose=2
)

# 1) Fit the RF grid
rf_grid.fit(X_train_tif['cleaned'], y_train_tif)

# 2) Inspect best params & CV score
print("Best params:", rf_grid.best_params_)
print("Best CV f1_weighted:", rf_grid.best_score_)

# 3) Evaluate on held-out test set
from sklearn.metrics import classification_report, confusion_matrix

y_pred = rf_grid.predict(X_test_tif['cleaned'])
print(classification_report(y_test_tif, y_pred))
print(confusion_matrix(y_test_tif, y_pred))


Fitting 3 folds for each of 144 candidates, totalling 432 fits
Best params: {'clf__max_depth': None, 'clf__max_features': 'sqrt', 'clf__n_estimators': 200, 'vect__binary': False, 'vect__max_df': 0.75, 'vect__ngram_range': (2, 7)}
Best CV f1_weighted: 0.9628675102006427
                          precision    recall  f1-score   support

          Not Vulnerable       0.97      0.94      0.95      2429
SQL Injection Vulnerable       0.97      0.99      0.98      2375
          XSS Vulnerable       0.97      0.98      0.98      2396

                accuracy                           0.97      7200
               macro avg       0.97      0.97      0.97      7200
            weighted avg       0.97      0.97      0.97      7200

[[2273   84   72]
 [  33 2342    0]
 [  37    0 2359]]


### linear svc tuned

In [ ]:
# from sklearn.pipeline import Pipeline
# from sklearn.model_selection import GridSearchCV
# from sklearn.feature_extraction.text import TfidfVectorizer
# from sklearn.svm import LinearSVC
# from sklearn.metrics import classification_report, confusion_matrix

# # 1) Build a fresh pipeline for LinearSVC
# lsvc_pipeline = Pipeline([
#     ('vect', TfidfVectorizer(
#         lowercase=False,
#         token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
#         stop_words=[';']
#     )),
#     ('clf', LinearSVC(dual=False, random_state=45))
# ])

# # 2) Define the hyper‐parameter grid
# lsvc_param_grid = {
#     'vect__ngram_range': [(2,5), (2,7)],
#     'clf__C': [0.01, 0.1, 1, 10],
#     'clf__max_iter': [1000, 5000]
# }

# # 3) Set up GridSearchCV
# lsvc_grid = GridSearchCV(
#     lsvc_pipeline,
#     lsvc_param_grid,
#     cv=3,
#     scoring='f1_weighted',
#     n_jobs=-1,
#     verbose=2
# )

# # 4) Fit on your full training set
# lsvc_grid.fit(X_train_tif['cleaned'], y_train_tif)

# # 5) Inspect best params & CV score
# print("Best LinearSVC params:", lsvc_grid.best_params_)
# print("Best CV f1_weighted:", lsvc_grid.best_score_)

# # 6) Evaluate on held-out test set
# y_pred = lsvc_grid.predict(X_test_tif['cleaned'])
# print(classification_report(y_test_tif, y_pred))
# print(confusion_matrix(y_test_tif, y_pred))


## linear svc tuned +calibrATED


In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.svm import LinearSVC
from sklearn.calibration import CalibratedClassifierCV
from sklearn.metrics import classification_report, confusion_matrix

# 1) Pipeline awal (buat GridSearch)
lsvc_pipeline = Pipeline([
    ('vect', TfidfVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';']
    )),
    ('clf', LinearSVC(dual=False, random_state=45))
])

# 2) Parameter grid (TETEP ADA, ga dihapus)
lsvc_param_grid = {
    'vect__ngram_range': [(2,5), (2,7)],
    'clf__C': [0.01, 0.1, 1, 10],
    'clf__max_iter': [1000, 5000]
}

# 3) GridSearchCV
lsvc_grid = GridSearchCV(
    lsvc_pipeline,
    lsvc_param_grid,
    cv=3,
    scoring='f1_weighted',
    n_jobs=-1,
    verbose=2
)

# 4) Fit GridSearch
lsvc_grid.fit(X_train_tif['cleaned'], y_train_tif)

print("Best LinearSVC params:", lsvc_grid.best_params_)
print("Best CV f1_weighted:", lsvc_grid.best_score_)

# 5) Build pipeline baru pakai CalibratedClassifierCV
best_params = lsvc_grid.best_params_

lsvc_best = LinearSVC(
    C=best_params['clf__C'],
    max_iter=best_params['clf__max_iter'],
    dual=False,
    random_state=45
)

calibrated_lsvc = CalibratedClassifierCV(
    estimator=lsvc_best,
    method='sigmoid',
    cv=3
)

calib_pipeline = Pipeline([
    ('vect', TfidfVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';'],
        ngram_range=best_params['vect__ngram_range']
    )),
    ('clf', calibrated_lsvc)
])

# 6) Fit pipeline calibrated
calib_pipeline.fit(X_train_tif['cleaned'], y_train_tif)

# 7) Evaluasi
y_pred = calib_pipeline.predict(X_test_tif['cleaned'])
print(classification_report(y_test_tif, y_pred))
print(confusion_matrix(y_test_tif, y_pred))

# probabilitas (udah bisa karena calibrated)
y_proba = calib_pipeline.predict_proba(X_test_tif['cleaned'])


Fitting 3 folds for each of 16 candidates, totalling 48 fits
Best LinearSVC params: {'clf__C': 10, 'clf__max_iter': 1000, 'vect__ngram_range': (2, 7)}
Best CV f1_weighted: 0.9844717980794928
                          precision    recall  f1-score   support

          Not Vulnerable       1.00      0.97      0.98      2429
SQL Injection Vulnerable       0.99      1.00      0.99      2375
          XSS Vulnerable       0.98      1.00      0.99      2396

                accuracy                           0.99      7200
               macro avg       0.99      0.99      0.99      7200
            weighted avg       0.99      0.99      0.99      7200

[[2346   33   50]
 [   5 2370    0]
 [   5    0 2391]]


### gaussian naive bayes tuned

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.preprocessing import FunctionTransformer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import classification_report, confusion_matrix

# Tuning GaussianNB
# 1) Build a fresh pipeline
gnb_pipeline = Pipeline([
    ('vect', TfidfVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';']
    )),
    ('to_dense', FunctionTransformer(lambda X: X.toarray(), accept_sparse=True)),
    ('clf', GaussianNB())
])

# 2) Param grid (only var_smoothing is valid for GNB)
param_grid_gnb = {
    'vect__ngram_range': [(1,3), (2,5)],
    'vect__max_df': [0.75, 1.0],
    'clf__var_smoothing': [1e-9, 1e-8, 1e-7]
}

# 3) GridSearchCV
gnb_grid = GridSearchCV(
    gnb_pipeline,
    param_grid_gnb,
    cv=3,
    scoring='f1_weighted',
    n_jobs=-1,
    verbose=2,
    error_score='raise'
)

# 4) Fit
gnb_grid.fit(X_train_tif['cleaned'], y_train_tif)

# 5) Results
print("Best params:", gnb_grid.best_params_)
print("Best CV f1_weighted:", gnb_grid.best_score_)

# 6) Test-set performance
y_pred = gnb_grid.predict(X_test_tif['cleaned'])
print(classification_report(y_test_tif, y_pred))
print(confusion_matrix(y_test_tif, y_pred))


Fitting 3 folds for each of 12 candidates, totalling 36 fits
Best params: {'clf__var_smoothing': 1e-07, 'vect__max_df': 0.75, 'vect__ngram_range': (1, 3)}
Best CV f1_weighted: 0.9602539783272374
                          precision    recall  f1-score   support

          Not Vulnerable       1.00      0.89      0.94      2429
SQL Injection Vulnerable       0.94      1.00      0.97      2375
          XSS Vulnerable       0.95      1.00      0.98      2396

                accuracy                           0.96      7200
               macro avg       0.96      0.96      0.96      7200
            weighted avg       0.96      0.96      0.96      7200

[[2152  163  114]
 [   1 2374    0]
 [   1    0 2395]]


### Multinomial naive bayes tuned

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import classification_report, confusion_matrix

# Tuning MNB
# 1) Define the pipeline
mnb_pipeline = Pipeline([
    ('vect', TfidfVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';']
    )),
    ('clf', MultinomialNB())
])

# 2) Define hyperparameter grid
mnb_param_grid = {
    'vect__ngram_range': [(1,3), (2,5)],
    'clf__alpha': [0.1, 0.5, 1.0]
}

# 3) Setup GridSearchCV
mnb_grid = GridSearchCV(
    mnb_pipeline,
    mnb_param_grid,
    cv=3,
    scoring='f1_weighted',
    n_jobs=-1,
    verbose=2
)

# 4) Train the model
mnb_grid.fit(X_train_tif['cleaned'], y_train_tif)

# 5) Output best params and score
print("Best MultinomialNB params:", mnb_grid.best_params_)
print("Best CV f1_weighted:", mnb_grid.best_score_)

# 6) Evaluate on test data
y_pred = mnb_grid.predict(X_test_tif['cleaned'])
print(classification_report(y_test_tif, y_pred))
print(confusion_matrix(y_test_tif, y_pred))


Fitting 3 folds for each of 6 candidates, totalling 18 fits
Best MultinomialNB params: {'clf__alpha': 0.1, 'vect__ngram_range': (2, 5)}
Best CV f1_weighted: 0.9525642155243029
                          precision    recall  f1-score   support

          Not Vulnerable       1.00      0.87      0.93      2429
SQL Injection Vulnerable       0.93      1.00      0.96      2375
          XSS Vulnerable       0.95      1.00      0.97      2396

                accuracy                           0.96      7200
               macro avg       0.96      0.96      0.96      7200
            weighted avg       0.96      0.96      0.96      7200

[[2120  173  136]
 [   1 2374    0]
 [   1    0 2395]]


### Decision tree tuned

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import classification_report, confusion_matrix

# Tuning Decision Tree
# 1) Build a fresh pipeline
dtc_pipeline = Pipeline([
    ('vect', TfidfVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';']
    )),
    ('clf', DecisionTreeClassifier(random_state=45))
])

# 2) Param grid for Decision Tree
param_grid_dtc = {
    'vect__ngram_range': [(1,3), (2,5)],
    'vect__max_df': [0.75, 1.0],
    'clf__max_depth': [None, 10, 20, 50],
    'clf__min_samples_split': [2, 5, 10],
    'clf__criterion': ['gini', 'entropy']
}

# 3) GridSearchCV
dtc_grid = GridSearchCV(
    dtc_pipeline,
    param_grid_dtc,
    cv=3,
    scoring='f1_weighted',
    n_jobs=-1,
    verbose=2,
    error_score='raise'
)

# 4) Fit
dtc_grid.fit(X_train_tif['cleaned'], y_train_tif)

# 5) Results
print("Best params:", dtc_grid.best_params_)
print("Best CV f1_weighted:", dtc_grid.best_score_)

# 6) Test-set performance
y_pred = dtc_grid.predict(X_test_tif['cleaned'])
print(classification_report(y_test_tif, y_pred))
print(confusion_matrix(y_test_tif, y_pred))


Fitting 3 folds for each of 96 candidates, totalling 288 fits
Best params: {'clf__criterion': 'gini', 'clf__max_depth': None, 'clf__min_samples_split': 2, 'vect__max_df': 0.75, 'vect__ngram_range': (1, 3)}
Best CV f1_weighted: 0.9558181686185351
                          precision    recall  f1-score   support

          Not Vulnerable       0.95      0.94      0.94      2429
SQL Injection Vulnerable       0.96      0.98      0.97      2375
          XSS Vulnerable       0.97      0.96      0.97      2396

                accuracy                           0.96      7200
               macro avg       0.96      0.96      0.96      7200
            weighted avg       0.96      0.96      0.96      7200

[[2279   85   65]
 [  38 2337    0]
 [  85    0 2311]]


# exporting models and vectorizer fot tf-idf tuned and not tuned

In [ ]:
import os
import cloudpickle

# Base directory on Google Drive
BASE_DIR = '/content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf'
os.makedirs(BASE_DIR, exist_ok=True)

# assign pipeline calibrated LSVC (biar konsisten nama kaya yang lain)
LSVC_vec_tf_idf_TUN = calib_pipeline

model_dict = {
    'gnb_pipeline_FINTUN_tf': gnb_grid.best_estimator_,
    'mnb_pipeline_FINTUN_tf': mnb_grid.best_estimator_,
    'dtc_pipeline_FINTUN_tf': dtc_grid.best_estimator_,
    'rf_pipeline_FINTUN_tf': rf_grid.best_estimator_,
    'lsvc_pipeline_FINTUN_tf': LSVC_vec_tf_idf_TUN,   # << calibrated pipeline masuk sini
}

for name, pipeline in model_dict.items():
    # 1. Save full pipeline
    pipeline_path = os.path.join(BASE_DIR, f'{name}.pkl')
    with open(pipeline_path, 'wb') as f:
        cloudpickle.dump(pipeline, f)
    print(f"✅ Saved pipeline → {pipeline_path}")

    # 2. Save vectorizer from the pipeline
    vect = pipeline.named_steps['vect']
    vect_path = os.path.join(BASE_DIR, f'vect_{name}.pkl')
    with open(vect_path, 'wb') as f:
        cloudpickle.dump(vect, f)
    print(f"✅ Saved vectorizer → {vect_path}")


✅ Saved pipeline → /content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf/gnb_pipeline_FINTUN_tf.pkl
✅ Saved vectorizer → /content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf/vect_gnb_pipeline_FINTUN_tf.pkl
✅ Saved pipeline → /content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf/mnb_pipeline_FINTUN_tf.pkl
✅ Saved vectorizer → /content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf/vect_mnb_pipeline_FINTUN_tf.pkl
✅ Saved pipeline → /content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf/dtc_pipeline_FINTUN_tf.pkl
✅ Saved vectorizer → /content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf/vect_dtc_pipeline_FINTUN_tf.pkl
✅ Saved pipeline → /content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf/rf_pipeline_FINTUN_tf.pkl
✅ Saved vectorizer → /content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf/vect_rf_pipeline_FINTUN_tf.pkl
✅ Saved pipeline → /content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf/lsvc_pipeline_FINTUN_tf.pkl
✅ Saved vectorizer → /content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf/vect_lsvc_pipeline

In [ ]:
import os
import cloudpickle

# Base directory on Google Drive
BASE_DIR = '/content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_tfidf'
os.makedirs(BASE_DIR, exist_ok=True)

# Map short names to your trained models
models_to_save = {
    'gnb_model_FIN_tf'  : GNB_vec_tf_idf,
    'mnb_model_FIN_tf'  : MNB_vec_tf_idf,
    'dtc_model_FIN_tf'  : DTC_vec_tf_idf,
    'rf_model_FIN_tf'   : RFC_vec_tf_idf,
    'lsvc_model_FIN_tf': LSVC_vec_tf_idf,
    'tfidf_vect_FIN_tf' : vecto_tf  # Save vectorizer too!
}

# Dump each with cloudpickle
for name, model in models_to_save.items():
    path = os.path.join(BASE_DIR, f'{name}.pkl')
    with open(path, 'wb') as f:
        cloudpickle.dump(model, f)
    print(f"Saved → {path}")


Saved → /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_tfidf/gnb_model_FIN_tf.pkl
Saved → /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_tfidf/mnb_model_FIN_tf.pkl
Saved → /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_tfidf/dtc_model_FIN_tf.pkl
Saved → /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_tfidf/rf_model_FIN_tf.pkl
Saved → /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_tfidf/lsvc_model_FIN_tf.pkl
Saved → /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_tfidf/tfidf_vect_FIN_tf.pkl


### fine tune testing

In [ ]:
# import cloudpickle

# def predict_code_finetuned(code_input: str):
#     BASE_PATH = '/content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf'

#     # Load models
#     gnb_model = cloudpickle.load(open(f"{BASE_PATH}/gnb_pipeline_FINTUN_tf.pkl", "rb"))
#     mnb_model = cloudpickle.load(open(f"{BASE_PATH}/mnb_pipeline_FINTUN_tf.pkl", "rb"))
#     dtc_model = cloudpickle.load(open(f"{BASE_PATH}/dtc_pipeline_FINTUN_tf.pkl", "rb"))
#     rf_model  = cloudpickle.load(open(f"{BASE_PATH}/rf_pipeline_FINTUN_tf.pkl", "rb"))
#     lsvc_model = cloudpickle.load(open(f"{BASE_PATH}/lsvc_pipeline_FINTUN_tf.pkl", "rb"))

#     # Load vectorizers
#     gnb_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_gnb_pipeline_FINTUN_tf.pkl", "rb"))
#     mnb_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_mnb_pipeline_FINTUN_tf.pkl", "rb"))
#     dtc_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_dtc_pipeline_FINTUN_tf.pkl", "rb"))
#     rf_vectorizer  = cloudpickle.load(open(f"{BASE_PATH}/vect_rf_pipeline_FINTUN_tf.pkl", "rb"))
#     lsvc_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_lsvc_pipeline_FINTUN_tf.pkl", "rb"))

#     # Main vectorizer (kalau masih kepake)
#     main_tf_untuned_vec = cloudpickle.load(open(
#         "/content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_tfidf/tfidf_vect_FIN_tf.pkl", "rb"
#     ))

#     # Preprocessing sama kaya waktu training
#     processed = process_php_tokenized(code_input)
#     processed = [processed]

#     # Transform input
#     # gnb_X = gnb_vectorizer.transform([processed]).toarray()   # GNB butuh dense
#     # mnb_X = mnb_vectorizer.transform([processed])
#     # dtc_X = dtc_vectorizer.transform([processed])
#     # rf_X  = rf_vectorizer.transform([processed])
#     # lsvc_X = lsvc_vectorizer.transform([processed])
#     gnb_X = processed
#     mnb_X = processed
#     dtc_X = processed
#     rf_X  = processed
#     lsvc_X = processed

#     print("🔍 Prediksi model fine-tuned + probabilitas:")

#     # GaussianNB
#     gnb_pred = gnb_model.predict(gnb_X)[0]
#     gnb_proba = gnb_model.predict_proba(gnb_X)[0]
#     print(f"🧪 GaussianNB       : {gnb_pred} | proba={gnb_proba}")

#     # MultinomialNB
#     mnb_pred = mnb_model.predict(mnb_X)[0]
#     mnb_proba = mnb_model.predict_proba(mnb_X)[0]
#     print(f"🧪 MultinomialNB    : {mnb_pred} | proba={mnb_proba}")

#     # DecisionTree
#     dtc_pred = dtc_model.predict(dtc_X)[0]
#     dtc_proba = dtc_model.predict_proba(dtc_X)[0]
#     print(f"🧪 DecisionTree     : {dtc_pred} | proba={dtc_proba}")

#     # RandomForest
#     rf_pred = rf_model.predict(rf_X)[0]
#     rf_proba = rf_model.predict_proba(rf_X)[0]
#     print(f"🧪 RandomForest     : {rf_pred} | proba={rf_proba}")

#     # LinearSVC (calibrated, udah ada predict_proba)
#     lsvc_pred = lsvc_model.predict(lsvc_X)[0]
#     lsvc_proba = lsvc_model.predict_proba(lsvc_X)[0]
#     print(f"🧪 LinearSVC (Calib): {lsvc_pred} | proba={lsvc_proba}")


In [ ]:
import cloudpickle
import numpy as np

def predict_code_finetuned(code_input: str):
    BASE_PATH = '/content/drive/MyDrive/REVISI_NEW_MODEL/tuned_tfidf'

    # === Load pipelines ===
    gnb_model = cloudpickle.load(open(f"{BASE_PATH}/gnb_pipeline_FINTUN_tf.pkl", "rb"))
    mnb_model = cloudpickle.load(open(f"{BASE_PATH}/mnb_pipeline_FINTUN_tf.pkl", "rb"))
    dtc_model = cloudpickle.load(open(f"{BASE_PATH}/dtc_pipeline_FINTUN_tf.pkl", "rb"))
    rf_model  = cloudpickle.load(open(f"{BASE_PATH}/rf_pipeline_FINTUN_tf.pkl", "rb"))
    lsvc_model = cloudpickle.load(open(f"{BASE_PATH}/lsvc_pipeline_FINTUN_tf.pkl", "rb"))

    # === Load vectorizers ===
    gnb_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_gnb_pipeline_FINTUN_tf.pkl", "rb"))
    mnb_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_mnb_pipeline_FINTUN_tf.pkl", "rb"))
    dtc_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_dtc_pipeline_FINTUN_tf.pkl", "rb"))
    rf_vectorizer  = cloudpickle.load(open(f"{BASE_PATH}/vect_rf_pipeline_FINTUN_tf.pkl", "rb"))
    lsvc_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_lsvc_pipeline_FINTUN_tf.pkl", "rb"))

    # === Preprocess ===
    processed = process_php_tokenized(code_input)

    # transform dengan masing² vectorizer
    processed = process_php_tokenized(code_input)
    processed = [processed]

    # Transform input
    # gnb_X = gnb_vectorizer.transform([processed]).toarray()   # GNB butuh dense
    # mnb_X = mnb_vectorizer.transform([processed])
    # dtc_X = dtc_vectorizer.transform([processed])
    # rf_X  = rf_vectorizer.transform([processed])
    # lsvc_X = lsvc_vectorizer.transform([processed])
    gnb_X = processed
    mnb_X = processed
    dtc_X = processed
    rf_X  = processed
    lsvc_X = processed

    models = {
        "GaussianNB": (gnb_model, gnb_X),
        "MultinomialNB": (mnb_model, mnb_X),
        "DecisionTree": (dtc_model, dtc_X),
        "RandomForest": (rf_model, rf_X),
        "LinearSVC": (lsvc_model, lsvc_X),
    }

    print("Vulnerability Detection with TF-IDF FINE TUNED:")
    for name, (model, X_input) in models.items():
        try:
            # kalau ada predict_proba langsung
            probs = model.predict_proba(X_input)[0]
            classes = model.classes_
        except AttributeError:
            # fallback LinearSVC (kalau belum calibrated)
            if hasattr(model, "decision_function"):
                scores = model.decision_function(X_input)
                exp_scores = np.exp(scores - np.max(scores))
                probs = exp_scores / exp_scores.sum()
                classes = model.classes_
            else:
                pred = model.predict(X_input)[0]
                classes = model.classes_
                probs = [1.0 if c == pred else 0.0 for c in classes]

        # cetak hasil
        print(f"🧪 {name} results:")
        for cls, prob in zip(classes, probs):
            prob_scalar = np.ravel(prob)[0]   # biar scalar float
            print(f"   - {cls}: {prob_scalar*100:.2f}%")
        print()


In [ ]:
test_code = """
<?php
if (isset($_GET['id'])) {
    $id = $_GET['id'];
    $query = "SELECT * FROM users WHERE id = '$id'";
    $result = mysqli_query($conn, $query);
}
?>
"""

predict_code_finetuned(test_code)


Vulnerability Detection with TF-IDF FINE TUNED:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 37.80%
   - SQL Injection Vulnerable: 62.19%
   - XSS Vulnerable: 0.01%

🧪 DecisionTree results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 28.50%
   - SQL Injection Vulnerable: 69.00%
   - XSS Vulnerable: 2.50%

🧪 LinearSVC results:
   - Not Vulnerable: 99.80%
   - SQL Injection Vulnerable: 0.18%
   - XSS Vulnerable: 0.02%



In [ ]:
import cloudpickle

def predict_code_nontuned(code_input: str):
    BASE_PATH = "/content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_tfidf"

    # Load models
    gnb_model = cloudpickle.load(open(f"{BASE_PATH}/gnb_model_FIN_tf.pkl", "rb"))
    mnb_model = cloudpickle.load(open(f"{BASE_PATH}/mnb_model_FIN_tf.pkl", "rb"))
    dtc_model = cloudpickle.load(open(f"{BASE_PATH}/dtc_model_FIN_tf.pkl", "rb"))
    rf_model  = cloudpickle.load(open(f"{BASE_PATH}/rf_model_FIN_tf.pkl", "rb"))
    lsvc_model = cloudpickle.load(open(f"{BASE_PATH}/lsvc_model_FIN_tf.pkl", "rb"))

    # Load vectorizer
    vectorizer = cloudpickle.load(open(f"{BASE_PATH}/tfidf_vect_FIN_tf.pkl", "rb"))

    # Preprocess input
    processed = process_php_tokenized(code_input)
    processed = str(processed)

    # Transform input
    X_input = vectorizer.transform([processed])

    # GNB needs dense format
    X_dense = X_input.toarray()

    # Predict using each model
    print("🔍 Prediksi model non-tuned:")
    print("🧪 GaussianNB       :", gnb_model.predict(X_dense)[0])
    print("🧪 MultinomialNB    :", mnb_model.predict(X_input)[0])
    print("🧪 DecisionTree     :", dtc_model.predict(X_input)[0])
    print("🧪 RandomForest     :", rf_model.predict(X_input)[0])
    print("🧪 LinearSVC        :", lsvc_model.predict(X_input)[0])


In [ ]:
code_example = """
<?php
$username = $_POST['user'];
$password = $_POST['pass'];
$query = "SELECT * FROM users WHERE user = '$username' AND pass = '$password'";
$result = mysqli_query($conn, $query);
?>
"""

predict_code_nontuned(code_example)


🔍 Prediksi model non-tuned:
🧪 GaussianNB       : SQL Injection Vulnerable
🧪 MultinomialNB    : SQL Injection Vulnerable
🧪 DecisionTree     : SQL Injection Vulnerable
🧪 RandomForest     : SQL Injection Vulnerable
🧪 LinearSVC        : Not Vulnerable


# Countvectorizer not tuned

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split

X_cv = dfin.drop(['vuln_type'], axis=1)
y_cv = dfin['vuln_type']
X_train_cv, X_test_cv, y_train_cv, y_test_cv = train_test_split(X_cv, y_cv, test_size=0.2, random_state=45)

vectorizer_cv = CountVectorizer(lowercase = False, ngram_range=(2,7), token_pattern = '[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+', stop_words=[';'], binary=True)

vecto_cv = vectorizer_cv.fit(X_train_cv['cleaned'])
X_train_vec_cv = vecto_cv.transform(X_train_cv['cleaned'])
X_test_vec_cv = vecto_cv.transform(X_test_cv['cleaned'])


In [ ]:
feat_name = []
feat_count = []
for x in vecto_cv.vocabulary_:
  print("[+] Feature(countvec): " + f"'{str(x)}'")
  feat_name.append(str(x))
  print("[+] Total of times appear in every dataset: " + str(vecto_cv.vocabulary_[x]))
  feat_count.append(vecto_cv.vocabulary_[x])
  print("\n")

type(vecto_cv.vocabulary_)

[+] Feature(countvec): '<?php $tainted'
[+] Total of times appear in every dataset: 8649


[+] Feature(countvec): '$tainted ='
[+] Total of times appear in every dataset: 2591


[+] Feature(countvec): '= filter_input(INPUT_GET,'
[+] Total of times appear in every dataset: 10122


[+] Feature(countvec): 'filter_input(INPUT_GET, t'
[+] Total of times appear in every dataset: 17622


[+] Feature(countvec): 't ,'
[+] Total of times appear in every dataset: 21991


[+] Feature(countvec): ', FILTER_SANITIZE_FULL_SPECIAL_CHARS);'
[+] Total of times appear in every dataset: 5909


[+] Feature(countvec): 'FILTER_SANITIZE_FULL_SPECIAL_CHARS); if(gettype($tainted)'
[+] Total of times appear in every dataset: 13022


[+] Feature(countvec): 'if(gettype($tainted) =='
[+] Total of times appear in every dataset: 19426


[+] Feature(countvec): '== string'
[+] Total of times appear in every dataset: 11352


[+] Feature(countvec): 'string )'
[+] Total of times appear in every dataset: 21537


[+] Feature

dict

## Gausian nb cv not tuned

In [ ]:
from sklearn.naive_bayes import GaussianNB
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from yellowbrick.classifier import ClassificationReport
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
GNB_vec_cv = GaussianNB()
GNB_vec_cv.fit(X_train_vec_cv.toarray(), y_train_cv)
print('--------------------- GaussianNB ( CODE ) ----------------------------')

y_pred = GNB_vec_cv.predict(X_test_vec_cv.toarray())

print(classification_report(y_test_cv, y_pred))
print('--------------------- confusion matrix  ----------------------------')
print(confusion_matrix(y_test_cv, y_pred))

y_true = y_test_cv
dt_pred = GNB_vec_cv.predict(X_test_vec_cv.toarray())
matrix = confusion_matrix(y_true, dt_pred)
print('-------------- TN FN TP FP --------------')
label_names = pd.Series(['XSS', 'SQL', 'Secure'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

--------------------- GaussianNB ( CODE ) ----------------------------
                          precision    recall  f1-score   support

          Not Vulnerable       1.00      0.89      0.94      2429
SQL Injection Vulnerable       0.94      1.00      0.97      2375
          XSS Vulnerable       0.96      1.00      0.98      2396

                accuracy                           0.96      7200
               macro avg       0.96      0.96      0.96      7200
            weighted avg       0.96      0.96      0.96      7200

--------------------- confusion matrix  ----------------------------
[[2161  162  106]
 [   4 2371    0]
 [   1    0 2395]]
-------------- TN FN TP FP --------------


Predicted XSS  Predicted SQL  Predicted Secure
Is XSS              2161            162               106
Is SQL                 4           2371                 0
Is Secure              1              0              2395

## Multinomial nb cv not tuned

In [ ]:
from sklearn.naive_bayes import MultinomialNB
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from yellowbrick.classifier import ClassificationReport
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
MNB_vec_cv = MultinomialNB()
MNB_vec_cv.fit(X_train_vec_cv.toarray(), y_train_cv)
print('--------------------- MultinomialNB ( CODE ) ----------------------------')

y_pred = MNB_vec_cv.predict(X_test_vec_cv.toarray())

print(classification_report(y_test_cv, y_pred))
print('--------------------- confusion matrix  ----------------------------')
print(confusion_matrix(y_test_cv, y_pred))

y_true = y_test_cv
dt_pred = MNB_vec_cv.predict(X_test_vec_cv.toarray())
matrix = confusion_matrix(y_true, dt_pred)
print('-------------- TN FN TP FP --------------')
label_names = pd.Series(['XSS', 'SQL', 'Secure'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

--------------------- MultinomialNB ( CODE ) ----------------------------
                          precision    recall  f1-score   support

          Not Vulnerable       1.00      0.75      0.85      2429
SQL Injection Vulnerable       0.92      1.00      0.96      2375
          XSS Vulnerable       0.85      1.00      0.92      2396

                accuracy                           0.91      7200
               macro avg       0.92      0.92      0.91      7200
            weighted avg       0.93      0.91      0.91      7200

--------------------- confusion matrix  ----------------------------
[[1812  201  416]
 [   0 2375    0]
 [   0    0 2396]]
-------------- TN FN TP FP --------------


Predicted XSS  Predicted SQL  Predicted Secure
Is XSS              1812            201               416
Is SQL                 0           2375                 0
Is Secure              0              0              2396

## Decision tree cv not tuned

In [ ]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from yellowbrick.classifier import ClassificationReport
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
DTC_vec_cv = DecisionTreeClassifier()
DTC_vec_cv.fit(X_train_vec_cv.toarray(), y_train_cv)
print('--------------------- DecisionTreeClassifier ( CODE ) ----------------------------')

y_pred = DTC_vec_cv.predict(X_test_vec_cv.toarray())

print(classification_report(y_test_cv, y_pred))
print('--------------------- confusion matrix  ----------------------------')
print(confusion_matrix(y_test_cv, y_pred))

y_true = y_test_cv
dt_pred = DTC_vec_cv.predict(X_test_vec_cv.toarray())
matrix = confusion_matrix(y_true, dt_pred)
print('-------------- TN FN TP FP --------------')
label_names = pd.Series(['XSS', 'SQL', 'Secure'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

--------------------- DecisionTreeClassifier ( CODE ) ----------------------------
                          precision    recall  f1-score   support

          Not Vulnerable       0.97      0.97      0.97      2429
SQL Injection Vulnerable       0.99      0.99      0.99      2375
          XSS Vulnerable       0.98      0.98      0.98      2396

                accuracy                           0.98      7200
               macro avg       0.98      0.98      0.98      7200
            weighted avg       0.98      0.98      0.98      7200

--------------------- confusion matrix  ----------------------------
[[2346   34   49]
 [  23 2352    0]
 [  53    0 2343]]
-------------- TN FN TP FP --------------


Predicted XSS  Predicted SQL  Predicted Secure
Is XSS              2346             34                49
Is SQL                23           2352                 0
Is Secure             53              0              2343

## Randomforest cv not tuned

In [ ]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from yellowbrick.classifier import ClassificationReport
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
RFC_vec_cv = RandomForestClassifier()
RFC_vec_cv.fit(X_train_vec_cv.toarray(), y_train_cv)
print('--------------------- RandomForestClassifier ( CODE ) ----------------------------')

y_pred = RFC_vec_cv.predict(X_test_vec_cv.toarray())

print(classification_report(y_test_cv, y_pred))
print('--------------------- confusion matrix  ----------------------------')
print(confusion_matrix(y_test_cv, y_pred))

y_true = y_test_cv
dt_pred = RFC_vec_cv.predict(X_test_vec_cv.toarray())
matrix = confusion_matrix(y_true, dt_pred)
print('-------------- TN FN TP FP --------------')
label_names = pd.Series(['XSS', 'SQL', 'Secure'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

--------------------- RandomForestClassifier ( CODE ) ----------------------------
                          precision    recall  f1-score   support

          Not Vulnerable       0.99      0.96      0.97      2429
SQL Injection Vulnerable       0.98      1.00      0.99      2375
          XSS Vulnerable       0.97      0.99      0.98      2396

                accuracy                           0.98      7200
               macro avg       0.98      0.98      0.98      7200
            weighted avg       0.98      0.98      0.98      7200

--------------------- confusion matrix  ----------------------------
[[2321   47   61]
 [  10 2365    0]
 [  24    0 2372]]
-------------- TN FN TP FP --------------


Predicted XSS  Predicted SQL  Predicted Secure
Is XSS              2321             47                61
Is SQL                10           2365                 0
Is Secure             24              0              2372

## Linear SVC cv not tuned

In [ ]:
from sklearn.svm import LinearSVC
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from yellowbrick.classifier import ClassificationReport
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
from sklearn.calibration import CalibratedClassifierCV

lsvc_CV = LinearSVC()
LSVC_vec_cv = CalibratedClassifierCV(lsvc_CV, cv=5)
LSVC_vec_cv.fit(X_train_vec_cv.toarray(), y_train_cv)
print('--------------------- LinearSVC ( CODE ) ----------------------------')

y_pred = LSVC_vec_cv.predict(X_test_vec_cv.toarray())

print(classification_report(y_test_cv, y_pred))
print('--------------------- confusion matrix  ----------------------------')
print(confusion_matrix(y_test_cv, y_pred))

y_true = y_test_cv
dt_pred = LSVC_vec_cv.predict(X_test_vec_cv.toarray())
matrix = confusion_matrix(y_true, dt_pred)
print('-------------- TN FN TP FP --------------')
label_names = pd.Series(['XSS', 'SQL', 'Secure'])
pd.DataFrame(matrix,
     columns='Predicted ' + label_names,
     index='Is ' + label_names)

/usr/local/lib/python3.12/dist-packages/sklearn/svm/_base.py:1249: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/sklearn/svm/_base.py:1249: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/sklearn/svm/_base.py:1249: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/sklearn/svm/_base.py:1249: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/sklearn/svm/_base.py:1249: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(


--------------------- LinearSVC ( CODE ) ----------------------------
                          precision    recall  f1-score   support

          Not Vulnerable       1.00      0.96      0.98      2429
SQL Injection Vulnerable       0.99      1.00      0.99      2375
          XSS Vulnerable       0.98      1.00      0.99      2396

                accuracy                           0.99      7200
               macro avg       0.99      0.99      0.99      7200
            weighted avg       0.99      0.99      0.99      7200

--------------------- confusion matrix  ----------------------------
[[2337   34   58]
 [   3 2372    0]
 [   4    0 2392]]
-------------- TN FN TP FP --------------


Predicted XSS  Predicted SQL  Predicted Secure
Is XSS              2337             34                58
Is SQL                 3           2372                 0
Is Secure              4              0              2392

## CV models classifier

In [ ]:
# def predict_code_no_feature_cv(strig):
#     data = strig
#     data = process_php_tokenized(data)
#     #print(data)
#     X_testt = vecto_cv.transform([data])
#     X_testt = X_testt.toarray()
#     # predict linear svc
#     lsvc_pred = LSVC_vec_cv.predict(X_testt)
#     # predict random forest
#     rfc_pred = RFC_vec_cv.predict(X_testt)
#     # predict decision tree
#     dtc_pred = DTC_vec_cv.predict(X_testt)
#     # predict multinomial nb
#     mnb_pred = MNB_vec_cv.predict(X_testt)
#     # predict gaussian nb
#     gnb_pred = GNB_vec_cv.predict(X_testt)
#     print("GaussianNB Classification (cv): " + gnb_pred[0])
#     print("MultinomialNB Classification(cv): " + mnb_pred[0])
#     print("DecisionTreeClassifier Classification(cv): " + dtc_pred[0])
#     print("RandomForestClassifier Classification(cv): " + rfc_pred[0])
#     print("LinearSVC Classification(cv): " + lsvc_pred[0])




In [ ]:
def predict_code_no_feature_cv(strig):
    data = process_php_tokenized(strig)
    X_testt = vecto_cv.transform([data])
    X_testt_dense = X_testt.toarray()  # buat GNB

    models = {
        "GaussianNB": GNB_vec_cv,
        "MultinomialNB": MNB_vec_cv,
        "DecisionTree": DTC_vec_cv,
        "RandomForest": RFC_vec_cv,
        "LinearSVC": LSVC_vec_cv,
    }

    print("Vulnerability Detection with Countved:")
    for name, model in models.items():
        try:
            # model dengan predict_proba
            probs = model.predict_proba(X_testt_dense if name=="GaussianNB" else X_testt)[0]
            classes = model.classes_
        except AttributeError:
            # fallback LinearSVC
            if hasattr(model, "decision_function"):
                scores = model.decision_function(X_testt)
                exp_scores = np.exp(scores - np.max(scores))
                probs = exp_scores / exp_scores.sum()
                classes = model.classes_
            else:
                pred = model.predict(X_testt)[0]
                classes = model.classes_
                probs = [1.0 if c == pred else 0.0 for c in classes]

        # cetak semua probabilitas tiap kelas
        print(f"🧪 {name} results:")
        for cls, prob in zip(classes, probs):
            prob_scalar = np.ravel(prob)[0]   # pastikan jadi 1 float
            print(f"   - {cls}: {prob_scalar*100:.2f}%")
        print()

In [ ]:
# CVE-2025-25403
test_code = """
<?php
/**
 * Copyright (C) 2007,2008  Arie Nugraha (dicarve@yahoo.com)
 *
 * This program is free software; you can redistribute it and/or modify
 * it under the terms of the GNU General Public License as published by
 * the Free Software Foundation; either version 3 of the License, or
 * (at your option) any later version.
 *
 * This program is distributed in the hope that it will be useful,
 * but WITHOUT ANY WARRANTY; without even the implied warranty of
 * MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
 * GNU General Public License for more details.
 *
 * You should have received a copy of the GNU General Public License
 * along with this program; if not, write to the Free Software
 * Foundation, Inc., 51 Franklin Street, Fifth Floor, Boston, MA  02110-1301  USA
 *
 */

/* Collection Type Management section */

// key to authenticate
define('INDEX_AUTH', '1');
// key to get full database access
define('DB_ACCESS', 'fa');

// main system configuration
require '../../../sysconfig.inc.php';
// IP based access limitation
require LIB.'ip_based_access.inc.php';
do_checkIP('smc');
do_checkIP('smc-masterfile');
// start the session
require SB.'admin/default/session.inc.php';
require SB.'admin/default/session_check.inc.php';
require SIMBIO.'simbio_GUI/table/simbio_table.inc.php';
require SIMBIO.'simbio_GUI/form_maker/simbio_form_table_AJAX.inc.php';
require SIMBIO.'simbio_GUI/paging/simbio_paging.inc.php';
require SIMBIO.'simbio_DB/datagrid/simbio_dbgrid.inc.php';
require SIMBIO.'simbio_DB/simbio_dbop.inc.php';

// privileges checking
$can_read = utility::havePrivilege('master_file', 'r');
$can_write = utility::havePrivilege('master_file', 'w');

if (!$can_read) {
    die('<div class="errorBox">'.__('You don\'t have enough privileges to view this section').'</div>');
}

/* RECORD OPERATION */
if (isset($_POST['saveData'])) {
    $collTypeName = trim(strip_tags($_POST['collTypeName']));
    // check form validity
    if (empty($collTypeName)) {
        utility::jsToastr(__('Collection Type'),__('Collection type name can\'t be empty'),'error');
        exit();
    } else {
        $data['coll_type_name'] = $dbs->escape_string($collTypeName);
        $data['input_date'] = date('Y-m-d');
        $data['last_update'] = date('Y-m-d');

        // create sql op object
        $sql_op = new simbio_dbop($dbs);
        if (isset($_POST['updateRecordID'])) {
            /* UPDATE RECORD MODE */
            // remove input date
            unset($data['input_date']);
            // filter update record ID
            $updateRecordID = (integer)$_POST['updateRecordID'];
            // update the data
            $update = $sql_op->update('mst_coll_type', $data, 'coll_type_id='.$updateRecordID);
            if ($update) {
                utility::jsToastr(__('Collection Type'),__('Colllection Type Data Successfully Updated'),'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(parent.jQuery.ajaxHistory[0].url);</script>';
            } else { utility::jsToastr(__('Collection Type'),__('Colllection Type Data FAILED to Updated. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error); }
            exit();
        } else {
            /* INSERT RECORD MODE */
            // insert the data
            $insert = $sql_op->insert('mst_coll_type', $data);
            if ($insert) {
                utility::jsToastr(__('Collection Type'),__('New Colllection Type Data Successfully Saved'),'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
            } else { utility::jsToastr(__('Collection Type'),__('Author Data FAILED to Save. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error,'error'); }
            exit();
        }
    }
    exit();
} else if (isset($_POST['itemID']) AND !empty($_POST['itemID']) AND isset($_POST['itemAction'])) {
    if (!($can_read AND $can_write)) {
        die();
    }
    /* DATA DELETION PROCESS */
    $sql_op = new simbio_dbop($dbs);
    $failed_array = array();
    $error_num = 0;
    if (!is_array($_POST['itemID'])) {
        // make an array
        $_POST['itemID'] = array((integer)$_POST['itemID']);
    }
    // loop array
    foreach ($_POST['itemID'] as $itemID) {
        $itemID = (integer)$itemID;
        // check if this item data still have an item
        $item_q = $dbs->query('SELECT ct.coll_type_name, COUNT(item_id) FROM item AS i
            LEFT JOIN mst_coll_type AS ct ON i.coll_type_id=ct.coll_type_id
            WHERE i.coll_type_id='.$itemID.' GROUP BY i.coll_type_id');
        $item_d = $item_q->fetch_row();
        if ($item_d[1] < 1) {
            if (!$sql_op->delete('mst_coll_type', "coll_type_id=$itemID")) {
                $error_num++;
            }
        } else {
            $still_have_item[] = sprintf(__('Collection type %s still used by %s items'),$item_d[0],$item_d[1]);
            $error_num++;
        }
    }

    if ($still_have_item) {
        $undeleted_coll_types = '';
        foreach ($still_have_item as $coll_type) {
            $undeleted_coll_types .= $coll_type."\n";
        }
        utility::jsToastr(__('Collection Type'),__('Below data can not be deleted:').$undeleted_coll_types,'error');
        exit();
    }
    // error alerting
    if ($error_num == 0) {
        utility::jsToastr(__('Collection Type'),__('All Data Successfully Deleted'),'success');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    } else {
        utility::jsToastr(__('Collection Type'),__('Some or All Data NOT deleted successfully!\nPlease contact system administrator'),'warning');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    }
    exit();
}
/* RECORD OPERATION END */

/* search form */
?>
<div class="menuBox">
<div class="menuBoxInner masterFileIcon">
	<div class="per_title">
	    <h2><?php echo __('Collection Type'); ?></h2>
  </div>
	<div class="sub_section">
	  <div class="btn-group">
      <a href="<?php echo MWB; ?>master_file/coll_type.php" class="btn btn-default"><?php echo __('Collection Type List'); ?></a>
      <a href="<?php echo MWB; ?>master_file/coll_type.php?action=detail" class="btn btn-default"><?php echo __('Add New Collection Type'); ?></a>
	  </div>
    <form name="search" action="<?php echo MWB; ?>master_file/coll_type.php" id="search" method="get" class="form-inline"><?php echo __('Search'); ?>
    <input type="text" name="keywords" class="form-control col-md-3" />
    <input type="submit" id="doSearch" value="<?php echo __('Search'); ?>" class="s-btn btn btn-default" />
    </form>
  </div>
</div>
</div>
<?php
/* search form end */
/* main content */
if (isset($_POST['detail']) OR (isset($_GET['action']) AND $_GET['action'] == 'detail')) {
    if (!($can_read AND $can_write)) {
        die('<div class="errorBox">'.__('You don\'t have enough privileges to view this section').'</div>');
    }
    $itemID = (integer)isset($_POST['itemID'])?$_POST['itemID']:0;
    $rec_q = $dbs->query("SELECT * FROM mst_coll_type WHERE coll_type_id=$itemID");
    $rec_d = $rec_q->fetch_assoc();

    // create new instance
    $form = new simbio_form_table_AJAX('mainForm', $_SERVER['PHP_SELF'].'?'.$_SERVER['QUERY_STRING'], 'post');
    $form->submit_button_attr = 'name="saveData" value="'.__('Save').'" class="s-btn btn btn-default"';

    // form table attributes
    $form->table_attr = 'id="dataList" class="s-table table"';
    $form->table_header_attr = 'class="alterCell font-weight-bold"';
    $form->table_content_attr = 'class="alterCell2"';

    // edit mode flag set
    if ($rec_q->num_rows > 0) {
        $form->edit_mode = true;
        // record ID for delete process
        $form->record_id = $itemID;
        // form record title
        $form->record_title = $rec_d['coll_type_name'];
        // submit button attribute
        $form->submit_button_attr = 'name="saveData" value="'.__('Update').'" class="s-btn btn btn-primary"';
    }

    /* Form Element(s) */
    // coll_type_name
    $form->addTextField('text', 'collTypeName', __('Collection Type').'*', $rec_d['coll_type_name']??'', 'style="width: 60%;" class="form-control"');

    // edit mode messagge
    if ($form->edit_mode) {
        echo '<div class="infoBox">'.__('You are going to edit collection type data').' : <b>'.$rec_d['coll_type_name'].'</b>  <br />'.__('Last Update').' '.$rec_d['last_update'].'</div>'; //mfc
    }
    // print out the form object
    echo $form->printOut();
} else {
    /* COLLECTION TYPE LIST */
    // table spec
    $table_spec = 'mst_coll_type AS ct';

    // create datagrid
    $datagrid = new simbio_datagrid();
    if ($can_read AND $can_write) {
        $datagrid->setSQLColumn('ct.coll_type_id', 'ct.coll_type_name AS \''.__('Collection Type').'\'', 'ct.last_update AS \''.__('Last Update').'\'');
    } else {
        $datagrid->setSQLColumn('ct.coll_type_name AS \''.__('Collection Type').'\'', 'ct.last_update AS \''.__('Last Update').'\'');
    }
    $datagrid->setSQLorder('coll_type_name ASC');

    // change the record order
    if (isset($_GET['fld']) AND isset($_GET['dir'])) {
        $datagrid->setSQLorder("'".urldecode($_GET['fld'])."' ".$dbs->escape_string($_GET['dir']));
    }

    // is there any search
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
       $keywords = utility::filterData('keywords', 'get', true, true, true);
       $datagrid->setSQLCriteria("ct.coll_type_name LIKE '%$keywords%'");
    }

    // set table and table header attributes
    $datagrid->table_attr = 'id="dataList" class="s-table table"';
    $datagrid->table_header_attr = 'class="dataListHeader" style="font-weight: bold;"';
    // set delete proccess URL
    $datagrid->chbox_form_URL = $_SERVER['PHP_SELF'];

    // put the result into variables
    $datagrid_result = $datagrid->createDataGrid($dbs, $table_spec, 20, ($can_read AND $can_write));
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
        $msg = str_replace('{result->num_rows}', $datagrid->num_rows, __('Found <strong>{result->num_rows}</strong> from your keywords')); //mfc
        echo '<div class="infoBox">'.$msg.' : "'.htmlspecialchars($_GET['keywords']).'"</div>';
    }

    echo $datagrid_result;
}
/* main content end */

"""
predict_code_no_feature_cv(test_code)

Vulnerability Detection with Countved:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 DecisionTree results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 4.00%
   - SQL Injection Vulnerable: 90.00%
   - XSS Vulnerable: 6.00%

🧪 LinearSVC results:
   - Not Vulnerable: 4.65%
   - SQL Injection Vulnerable: 93.45%
   - XSS Vulnerable: 1.90%



In [ ]:
# CVE-2025-45818
test_code = """
<?php
/**
 * Copyright (C) 2009  Arie Nugraha (dicarve@yahoo.com)
 *
 * This program is free software; you can redistribute it and/or modify
 * it under the terms of the GNU General Public License as published by
 * the Free Software Foundation; either version 3 of the License, or
 * (at your option) any later version.
 *
 * This program is distributed in the hope that it will be useful,
 * but WITHOUT ANY WARRANTY; without even the implied warranty of
 * MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
 * GNU General Public License for more details.
 *
 * You should have received a copy of the GNU General Public License
 * along with this program; if not, write to the Free Software
 * Foundation, Inc., 51 Franklin Street, Fifth Floor, Boston, MA  02110-1301  USA
 *
 */

/* Item Status Management section */

// key to authenticate
define('INDEX_AUTH', '1');
// key to get full database access
define('DB_ACCESS', 'fa');

// main system configuration
require '../../../sysconfig.inc.php';
// IP based access limitation
require LIB.'ip_based_access.inc.php';
do_checkIP('smc');
do_checkIP('smc-masterfile');
// start the session
require SB.'admin/default/session.inc.php';
require SB.'admin/default/session_check.inc.php';
require SIMBIO.'simbio_GUI/table/simbio_table.inc.php';
require SIMBIO.'simbio_GUI/form_maker/simbio_form_table_AJAX.inc.php';
require SIMBIO.'simbio_GUI/paging/simbio_paging.inc.php';
require SIMBIO.'simbio_DB/datagrid/simbio_dbgrid.inc.php';
require SIMBIO.'simbio_DB/simbio_dbop.inc.php';

// privileges checking
$can_read = utility::havePrivilege('master_file', 'r');
$can_write = utility::havePrivilege('master_file', 'w');

if (!$can_read) {
    die('<div class="errorBox">'.__('You don\'t have enough privileges to access this area!').'</div>');
}

// item status rules
$rules_option[] = array(NO_LOAN_TRANSACTION, __('No Loan Transaction'));
$rules_option[] = array(SKIP_STOCK_TAKE, __('Skipped By Stock Take'));

/* RECORD OPERATION */
if (isset($_POST['saveData'])) {
    $itemStatusID = strip_tags(trim($_POST['itemStatusID']));
    $itemStatusName = strip_tags(trim($_POST['itemStatus']));
    // check form validity
    if (empty($itemStatusID) OR empty($itemStatusName)) {
        utility::jsToastr(__('Item Status'),__('Item Status ID and Name can\'t be empty'),'error');
        exit();
    } else {
        $data['item_status_id'] = $dbs->escape_string($itemStatusID);
        $data['item_status_name'] = $dbs->escape_string($itemStatusName);
        // parsing rules
		/*
        $rules = '';
        if (isset($_POST['rules']) AND !empty($_POST['rules'])) {
            $rules = serialize($_POST['rules']);
        } else {
            $rules = 'literal{NULL}';
        }
		*/
        $data['rules'] = 'literal{NULL}';
        $data['no_loan'] = '0';
        $data['skip_stock_take'] = '0';
        foreach ($_POST['rules']??[] as $rule) {
            if ((integer)$rule === NO_LOAN_TRANSACTION) $data['no_loan'] = '1';
            if ((integer)$rule === SKIP_STOCK_TAKE) $data['skip_stock_take'] = '1';
        }
        $data['input_date'] = date('Y-m-d');
        $data['last_update'] = date('Y-m-d');

        // create sql op object
        $sql_op = new simbio_dbop($dbs);
        if (isset($_POST['updateRecordID'])) {
            /* UPDATE RECORD MODE */
            // remove input date
            unset($data['input_date']);
            // filter update record ID
            $updateRecordID = $dbs->escape_string(trim($_POST['updateRecordID']));
            // update the data
            $update = $sql_op->update('mst_item_status', $data, 'item_status_id=\''.$updateRecordID.'\'');
            if ($update) {
                utility::jsToastr(__('Item Status'), __('New Item Status Data Successfully Updated'), 'success');
                // update item status ID in item table to keep data integrity
                $sql_op->update('item', array('item_status_id' => $data['item_status_id']), 'item_status_id=\''.$updateRecordID.'\'');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(parent.jQuery.ajaxHistory[0].url);</script>';
            } else {
                utility::jsToastr(__('Item Status'),__('Item Status Data FAILED to Updated. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error,'error');
            }
            exit();
        } else {
            /* INSERT RECORD MODE */
            // insert the data
            $insert = $sql_op->insert('mst_item_status', $data);
            if ($insert) {
                utility::jsToastr(__('Item Status'), __('New Item Status Data Successfully Saved'), 'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
            } else {
                utility::jsToastr(__('Item Status'), __('Item Status Data FAILED to Save. Please Contact System Administrator')."\n".$sql_op->error, 'error');
            }
            exit();
        }
    }
    exit();
} else if (isset($_POST['itemID']) AND !empty($_POST['itemID']) AND isset($_POST['itemAction'])) {
    if (!($can_read AND $can_write)) {
        die();
    }
    /* DATA DELETION PROCESS */
    $sql_op = new simbio_dbop($dbs);
    $failed_array = array();
    $error_num = 0;
    $still_have_item = array();
    if (!is_array($_POST['itemID'])) {
        // make an array
        $_POST['itemID'] = array($dbs->escape_string(trim($_POST['itemID'])));
    }
    // loop array
    foreach ($_POST['itemID'] as $itemID) {
        $itemID = $dbs->escape_string(trim($itemID));
        // check if this place data still in use items
        $_sql_status_item_q = sprintf('SELECT mis.item_status_name, COUNT(mis.item_status_id) FROM item AS i
        LEFT JOIN mst_item_status AS mis ON i.item_status_id=mis.item_status_id
        WHERE mis.item_status_id=%d GROUP BY mis.item_status_name', $itemID);
        $status_item_q = $dbs->query($_sql_status_item_q);
        $status_item_d = $status_item_q->fetch_row();
        if ($status_item_d[1] < 1) {
            if (!$sql_op->delete('mst_item_status', "item_status_id='$itemID'")) {
                $error_num++;
            }
        }else{
            $still_have_item[] = sprintf(__('%s still in use %d item ').'<br/>',substr($status_item_d[0], 0, 45),$status_item_d[1]);
            $error_num++;
        }
    }

    if ($still_have_item) {
        $titles = '';
        foreach ($still_have_item as $title) {
            $titles .= $title . "\n";
        }
        utility::jsToastr( __('Item Status'), __('Below data can not be deleted:') . "\n" . $titles, 'error');
        echo '<script type="text/javascript">parent.$(\'#mainContent\').simbioAJAX(\'' . $_SERVER['PHP_SELF'] . '\', {addData: \'' . $_POST['lastQueryStr'] . '\'});</script>';
        exit();
    }

    // error alerting
    if ($error_num == 0) {
        utility::jsToastr(__('Item Status'), __('All Data Successfully Deleted'), 'success');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    } else {
        utility::jsToastr(__('Item Status'), __('Some or All Data NOT deleted successfully!\nPlease contact system administrator'), 'warning');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    }
    exit();
}
/* item status update process end */

/* search form */
?>
<div class="menuBox">
<div class="menuBoxInner masterFileIcon">
	<div class="per_title">
	    <h2><?php echo __('Item Status'); ?></h2>
  </div>
	<div class="sub_section">
	  <div class="btn-group">
      <a href="<?php echo MWB; ?>master_file/item_status.php" class="btn btn-default"><?php echo __('Item Status'); ?></a>
		  <a href="<?php echo MWB; ?>master_file/item_status.php?action=detail" class="btn btn-default"><?php echo __('Add New Item Status'); ?></a>
	  </div>
    <form name="search" action="<?php echo MWB; ?>master_file/item_status.php" id="search" method="get" class="form-inline"><?php echo __('Search'); ?>
    <input type="text" name="keywords" class="form-control col-md-3" />
    <input type="submit" id="doSearch" value="<?php echo __('Search'); ?>" class="s-btn btn btn-default" />
    </form>
	</div>
</div>
</div>
<?php
/* search form end */
/* main content */
if (isset($_POST['detail']) OR (isset($_GET['action']) AND $_GET['action'] == 'detail')) {
    if (!($can_read AND $can_write)) {
        die('<div class="errorBox">'.__('You don\'t have enough privileges to access this area!').'</div>');
    }
    /* RECORD FORM */
    $itemID = trim($dbs->escape_string(isset($_POST['itemID'])?$_POST['itemID']:''));
    $rec_q = $dbs->query("SELECT * FROM mst_item_status WHERE item_status_id='$itemID'");
    $rec_d = $rec_q->fetch_assoc();

    // create new instance
    $form = new simbio_form_table_AJAX('mainForm', $_SERVER['PHP_SELF'].'?'.$_SERVER['QUERY_STRING'], 'post');
    $form->submit_button_attr = 'name="saveData" value="'.__('Save').'" class="s-btn btn btn-default"';

    // form table attributes
    $form->table_attr = 'id="dataList" class="s-table table"';
    $form->table_header_attr = 'class="alterCell font-weight-bold"';
    $form->table_content_attr = 'class="alterCell2"';

    // edit mode flag set
    if ($rec_q->num_rows > 0) {
        $form->edit_mode = true;
        // record ID for delete process
        $form->record_id = $itemID;
        // form record title
        $form->record_title = $rec_d['item_status_name'];
        // submit button attribute
        $form->submit_button_attr = 'name="saveData" value="'.__('Update').'" class="s-btn btn btn-primary"';
    }

    /* Form Element(s) */
    // item status code
    $form->addTextField('text', 'itemStatusID', __('Item Status Code').'*', $rec_d['item_status_id']??'', 'style="width: 20%;" maxlength="3" class="form-control"');
    // item status name
    $form->addTextField('text', 'itemStatus', __('Item Status Name').'*', $rec_d['item_status_name']??'', 'style="width: 60%;" class="form-control"');
    // item status rules
	$rules = array();

	if ($rec_d['no_loan']??false) $rules[] = NO_LOAN_TRANSACTION;

	if ($rec_d['skip_stock_take']??false) $rules[] = SKIP_STOCK_TAKE;

    $form->addCheckbox('rules', __('Rules'), $rules_option, $rules);

    // edit mode messagge
    if ($form->edit_mode) {
        echo '<div class="infoBox">'.__('You are going to edit Item Status data').' : <b>'.$rec_d['item_status_name'].'</b>  <br />'.__('Last Update').' '.$rec_d['last_update'].'</div>'; //mfc
    }
    // print out the form object
    echo $form->printOut();
} else {
    /* ITEM STATUS LIST */
    // table spec
    $table_spec = 'mst_item_status AS ist';

    // create datagrid
    $datagrid = new simbio_datagrid();
    if ($can_read AND $can_write) {
        $datagrid->setSQLColumn('ist.item_status_id',
            'ist.item_status_id AS \''.__('Item Status Code').'\'',
            'ist.item_status_name AS \''.__('Item Status Name').'\'',
            'ist.last_update AS \''.__('Last Update').'\'');
    } else {
        $datagrid->setSQLColumn('ist.item_status_id AS \''.__('Item Status Code').'\'',
            'ist.item_status_name AS \''.__('Item Status Name').'\'',
            'ist.last_update AS \''.__('Last Update').'\'');
    }
    $datagrid->setSQLorder('item_status_name ASC');

    // change the record order
    if (isset($_GET['fld']) AND isset($_GET['dir'])) {
        $datagrid->setSQLorder("'".urldecode($_GET['fld'])."' ".$dbs->escape_string($_GET['dir']));
    }

    // is there any search
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
       $keywords = utility::filterData('keywords', 'get', true, true, true);
       $datagrid->setSQLCriteria("ist.item_status_name LIKE '%$keywords%'");
    }

    // set table and table header attributes
    $datagrid->table_attr = 'id="dataList" class="s-table table"';
    $datagrid->table_header_attr = 'class="dataListHeader" style="font-weight: bold;"';
    // set delete proccess URL
    $datagrid->chbox_form_URL = $_SERVER['PHP_SELF'];

    // put the result into variables
    $datagrid_result = $datagrid->createDataGrid($dbs, $table_spec, 20, ($can_read AND $can_write));
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
        $msg = str_replace('{result->num_rows}', $datagrid->num_rows, __('Found <strong>{result->num_rows}</strong> from your keywords')); //mfc
        echo '<div class="infoBox">'.$msg.' : "'.htmlspecialchars($_GET['keywords']).'"</div>';
    }

    echo $datagrid_result;
}
/* main content end */
"""

predict_code_no_feature_cv(test_code)

Vulnerability Detection with Countved:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 DecisionTree results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 4.00%
   - SQL Injection Vulnerable: 91.00%
   - XSS Vulnerable: 5.00%

🧪 LinearSVC results:
   - Not Vulnerable: 4.64%
   - SQL Injection Vulnerable: 93.41%
   - XSS Vulnerable: 1.95%



In [ ]:
# CVE-2025-45819
test = """
<?php
/**
 * Copyright (C) 2007,2008  Arie Nugraha (dicarve@yahoo.com)
 *
 * This program is free software; you can redistribute it and/or modify
 * it under the terms of the GNU General Public License as published by
 * the Free Software Foundation; either version 3 of the License, or
 * (at your option) any later version.
 *
 * This program is distributed in the hope that it will be useful,
 * but WITHOUT ANY WARRANTY; without even the implied warranty of
 * MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
 * GNU General Public License for more details.
 *
 * You should have received a copy of the GNU General Public License
 * along with this program; if not, write to the Free Software
 * Foundation, Inc., 51 Franklin Street, Fifth Floor, Boston, MA  02110-1301  USA
 *
 */

/* Author Management section */

// key to authenticate
if (!defined('INDEX_AUTH')) {
  define('INDEX_AUTH', '1');
}
// key to get full database access
define('DB_ACCESS', 'fa');

// main system configuration
if (!defined('SB')) {
  require '../../../sysconfig.inc.php';
}

// IP based access limitation
require LIB.'ip_based_access.inc.php';
do_checkIP('smc');
do_checkIP('smc-masterfile');

// start the session
require SB.'admin/default/session.inc.php';
require SB.'admin/default/session_check.inc.php';
require SIMBIO.'simbio_GUI/table/simbio_table.inc.php';
require SIMBIO.'simbio_GUI/form_maker/simbio_form_table_AJAX.inc.php';
require SIMBIO.'simbio_GUI/paging/simbio_paging.inc.php';
require SIMBIO.'simbio_DB/datagrid/simbio_dbgrid.inc.php';
require SIMBIO.'simbio_DB/simbio_dbop.inc.php';

// privileges checking
$can_read = utility::havePrivilege('master_file', 'r');
$can_write = utility::havePrivilege('master_file', 'w');

if (!$can_read) {
    die('<div class="errorBox">'.__('You don\'t have enough privileges to access this area!').'</div>');
}

$in_pop_up = false;
// check if we are inside pop-up window
if (isset($_GET['inPopUp'])) {
  $in_pop_up = true;
}

/* RECORD OPERATION */
if (isset($_POST['saveData']) AND $can_read AND $can_write) {
    $authorName = trim(strip_tags($_POST['authorName']));
    // check form validity
    if (empty($authorName)) {
        utility::jsToastr(__('Author'),__('Author name can\'t be empty'),'warning');
        exit();
    } else {
        $data['author_name'] = $dbs->escape_string($authorName);
        $author_year = $dbs->escape_string(trim($_POST['authorYear']));
        if ($author_year) { $data['author_year'] = $author_year; }
        $data['authority_type'] = trim($dbs->escape_string(strip_tags($_POST['authorityType'])));
        $data['auth_list'] = trim($dbs->escape_string(strip_tags($_POST['authList'])));
        $data['input_date'] = date('Y-m-d');
        $data['last_update'] = date('Y-m-d');

        // create sql op object
        $sql_op = new simbio_dbop($dbs);
        if (isset($_POST['updateRecordID'])) {
            /* UPDATE RECORD MODE */
            // remove input date
            unset($data['input_date']);
            // filter update record ID
            $updateRecordID = (integer)$_POST['updateRecordID'];
            // update the data
            $update = $sql_op->update('mst_author', $data, 'author_id='.$updateRecordID);
            if ($update) {
                utility::writeLogs($dbs, 'staff', $_SESSION['uid'], 'Master file', $_SESSION['realname'].' update author ('.$data['author_name'].').', 'Author', 'update');
                utility::jsToastr(__('Author'),__('Author Data Successfully Updated'),'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(parent.jQuery.ajaxHistory[0].url);</script>';
                if ($in_pop_up) {
                    echo '<script type="text/javascript">top.setIframeContent(\'authorIframe\', \''.MWB.'bibliography/iframe_author.php?biblioID='.$_GET['biblio_id'].'\');</script>';
                    echo '<script type="text/javascript">top.jQuery.colorbox.close();</script>';
                } else {
                    echo '<script type="text/javascript">parent.$(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
                }
            } else { utility::jsToastr(__('Author'),__('Author Data FAILED to Updated. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error,'error'); }
            exit();
        } else {
            /* INSERT RECORD MODE */
            // insert the data
            $insert = $sql_op->insert('mst_author', $data);
            if ($insert) {
                utility::writeLogs($dbs, 'staff', $_SESSION['uid'], 'Master file', $_SESSION['realname'].' add new author ('.$data['author_name'].').', 'Author', 'Add');
                utility::jsToastr(__('Author'),__('New Author Data Successfully Saved'),'success');
                echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
                if ($in_pop_up) {
                    echo '<script type="text/javascript">top.setIframeContent(\'authorIframe\', \''.MWB.'bibliography/iframe_author.php?biblioID='.$_GET['biblio_id'].'\');</script>';
                    echo '<script type="text/javascript">top.jQuery.colorbox.close();</script>';
                } else {
                    echo '<script type="text/javascript">parent.$(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\');</script>';
                }

            } else {
                utility::writeLogs($dbs, 'staff', $_SESSION['uid'], 'Master file', $_SESSION['realname'].' can not add new author ('.$data['author_name'].').', 'Author', 'Fail');
                utility::jsToastr(__('Author'),__('Author Data FAILED to Save. Please Contact System Administrator')."\nDEBUG : ".$sql_op->error,'error');
            }
            exit();
        }
    }
    exit();
} else if (isset($_POST['itemID']) AND !empty($_POST['itemID']) AND isset($_POST['itemAction'])) {
    if (!($can_read AND $can_write)) {
        die();
    }
    /* DATA DELETION PROCESS */
    $sql_op = new simbio_dbop($dbs);
    $failed_array = array();
    $error_num = 0;
    $still_used_biblio = array();
    if (!is_array($_POST['itemID'])) {
        // make an array
        $_POST['itemID'] = array((integer)$_POST['itemID']);
    }
    // loop array
    foreach ($_POST['itemID'] as $itemID) {
        $itemID = (integer)$itemID;

        // check if this author data still used biblio
        $_sql_biblio_author_q = sprintf('SELECT  ma.author_name, COUNT(ma.author_id),b.title FROM biblio AS b
        LEFT JOIN biblio_author ba ON ba.biblio_id=b.biblio_id
        LEFT JOIN mst_author ma ON ma.author_id=ba.author_id
        WHERE ma.author_id=%d GROUP BY b.title', $itemID);
        $biblio_author_q = $dbs->query($_sql_biblio_author_q);
        $biblio_author_d = $biblio_author_q->fetch_row();
        $_log_authors .= $biblio_author_d['author_name'].', ';

        if ($biblio_author_d[1] < 1) {
            if (!$sql_op->delete('mst_author', 'author_id='.$itemID)) {
                $error_num++;
            }
        }
         else {
            $still_used_biblio[] = substr($biblio_author_d[0], 0, 6).'... still used biblio '.substr($biblio_author_d[2], 0, 6).' ..'."\n";
            $error_num++;
        }
    }

    if ($still_used_biblio) {
        $titles = '';
        foreach ($still_used_biblio as $title) {
          $titles .= $title."\n";
        }
        utility::jsToastr(__('Author'),__('Below data can not be deleted:')."\n".$titles, 'warning');
        echo '<script type="text/javascript">parent.$(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'\', {addData: \''.$_POST['lastQueryStr'].'\'});</script>';
        exit();
    }

    // error alerting
    if ($error_num == 0) {
        utility::writeLogs($dbs, 'staff', $_SESSION['uid'], 'Master file', $_SESSION['realname'].' delete  author ('.implode(', ', $_log_authors).').', 'Author', 'delete');
        utility::jsToastr(__('Author'),__('All Data Successfully Deleted'),'success');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    } else {
        utility::writeLogs($dbs, 'staff', $_SESSION['uid'], 'Master file', $_SESSION['realname'].' delete  author(s), BUT not all ('.implode(', ', $_log_authors).').', 'Author', 'delete');
        utility::jsToastr(__('Author'),__('Some or All Data NOT deleted successfully!\nPlease contact system administrator'),'error');
        echo '<script type="text/javascript">parent.jQuery(\'#mainContent\').simbioAJAX(\''.$_SERVER['PHP_SELF'].'?'.$_POST['lastQueryStr'].'\');</script>';
    }
    exit();
}
/* RECORD OPERATION END */

/* search form */
if (!$in_pop_up) {
?>
<div class="menuBox">
<div class="menuBoxInner masterFileIcon">
	<div class="per_title">
	    <h2><?php echo __('Author'); ?></h2>
  </div>
	<div class="sub_section">
	  <div class="btn-group">
      <a href="<?php echo MWB; ?>master_file/author.php" class="btn btn-default"><?php echo __('Author List'); ?></a>
      <a href="<?php echo MWB; ?>master_file/author.php?action=detail" class="btn btn-default"><?php echo __('Add New Author'); ?></a>
    </div>
    <form name="search" action="<?php echo MWB; ?>master_file/author.php" id="search" method="get" class="form-inline"><?php echo __('Search'); ?>
    <input type="text" name="keywords" class="form-control col-md-3" />
    <input type="submit" id="doSearch" value="<?php echo __('Search'); ?>" class="s-btn btn btn-default" />
    </form>
  </div>
</div>
</div>
<?php
}

/* search form end */
/* main content */
if (isset($_POST['detail']) OR (isset($_GET['action']) AND $_GET['action'] == 'detail')) {
    if (!($can_read AND $can_write)) {
        die('<div class="errorBox">'.__('You don\'t have enough privileges to access this area!').'</div>');
    }
    /* RECORD FORM */
    $itemID = (integer)isset($_POST['itemID'])?$_POST['itemID']:0;
    $rec_q = $dbs->query('SELECT * FROM mst_author WHERE author_id='.$itemID);
    $rec_d = $rec_q->fetch_assoc();

    // create new instance
    $form = new simbio_form_table_AJAX('authorForm', $_SERVER['PHP_SELF'].'?'.$_SERVER['QUERY_STRING'], 'post');
    $form->submit_button_attr = 'name="saveData" value="'.__('Save').'" class="s-btn btn btn-default"';

    // form table attributes
    $form->table_attr = 'id="dataList" class="s-table table"';
    $form->table_header_attr = 'class="alterCell font-weight-bold"';
    $form->table_content_attr = 'class="alterCell2"';

    // edit mode flag set
    if ($rec_q->num_rows > 0) {
        $form->edit_mode = true;
        // record ID for delete process
        if (!$in_pop_up) {
            $form->record_id = $itemID;
        } else {
            $form->addHidden('updateRecordID', $itemID);
            $form->back_button = false;
            $form->delete_button = false;
        }
        // form record title
        $form->record_title = $rec_d['author_name'];
        // submit button attribute
        $form->submit_button_attr = 'name="saveData" value="'.__('Update').'" class="s-btn btn btn-primary"';
    }

    /* Form Element(s) */
    // author name
    $form->addTextField('text', 'authorName', __('Author Name').'*', $rec_d['author_name']??'', ' class="form-control col-6"');
    // author year
    $form->addTextField('text', 'authorYear', __('Author Birth Year'), $rec_d['author_year']??'', ' class="form-control col-6"');
    // authority type
    foreach ($sysconf['authority_type'] as $auth_type_id => $auth_type) {
        $auth_type_options[] = array($auth_type_id, $auth_type);
    }
    $form->addSelectList('authorityType', __('Authority Type'), $auth_type_options, $rec_d['authority_type']??'',' class="form-control col-6"');
    // authority list
    $form->addTextField('text', 'authList', __('Authority Files'), $rec_d['auth_list']??'', ' class="form-control col-6"');

    // edit mode messagge
    if ($form->edit_mode) {
        echo '<div class="infoBox">'.__('You are going to edit author data').' : <b>'.$rec_d['author_name'].'</b> <br />'.__('Last Update').' '.$rec_d['last_update'].'</div>'; //mfc
    }
    // print out the form object
    echo $form->printOut();
} else {
    /* AUTHOR LIST */
    // table spec
    $sql_criteria = 'a.author_id > 0';
    if (isset($_GET['type']) && $_GET['type'] == 'orphaned') {
        $table_spec = 'mst_author AS a LEFT JOIN biblio_author AS ba ON a.author_id=ba.author_id';
        $sql_criteria = 'ba.biblio_id IS NULL OR ba.author_id IS NULL';
    } else {
        $table_spec = 'mst_author AS a';
    }


    // authority field num
    $auth_type_fld = 2;
    // create datagrid
    $datagrid = new simbio_datagrid();
    if ($can_read AND $can_write) {
        $auth_type_fld = 3;
        $datagrid->setSQLColumn('a.author_id', 'a.author_name AS \''.__('Author Name').'\'',
            'a.author_year AS \''.__('Author Year').'\'',
            'a.authority_type AS \''.__('Authority Type').'\'',
            'a.auth_list AS \''.__('Authority Files').'\'',
            'a.last_update AS \''.__('Last Update').'\'');
    } else {
        $datagrid->setSQLColumn('a.author_name AS \''.__('Author Name').'\'',
            'a.author_year AS \''.__('Author Year').'\'',
            'a.authority_type AS \''.__('Authority Type').'\'',
            'a.auth_list AS \''.__('Authority Files').'\'',
            'a.last_update AS \''.__('Last Update').'\'');
    }
    $datagrid->setSQLorder('author_name ASC');

    // change the record order
    if (isset($_GET['fld']) AND isset($_GET['dir'])) {
        $datagrid->setSQLorder("'".urldecode($_GET['fld'])."' ".$dbs->escape_string($_GET['dir']));
    }

    // is there any search
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
       $keywords = utility::filterData('keywords', 'get', true, true, true);
       $sql_criteria .= " AND a.author_name LIKE '%$keywords%'";
    }
    $datagrid->setSQLCriteria($sql_criteria);

    // set table and table header attributes
    $datagrid->table_attr = 'id="dataList" class="s-table table"';
    $datagrid->table_header_attr = 'class="dataListHeader" style="font-weight: bold;"';
    // set delete proccess URL
    $datagrid->chbox_form_URL = $_SERVER['PHP_SELF'];

    // callback function to change value of authority type
    function callbackAuthorType($obj_db, $rec_d)
    {
        global $sysconf, $auth_type_fld;
        return $sysconf['authority_type'][$rec_d[$auth_type_fld]];
    }
    // modify column content
    $datagrid->modifyColumnContent($auth_type_fld, 'callback{callbackAuthorType}');
    // put the result into variable
    $datagrid_result = $datagrid->createDataGrid($dbs, $table_spec, 20, ($can_read AND $can_write));
    if (isset($_GET['keywords']) AND $_GET['keywords']) {
        $msg = str_replace('{result->num_rows}', $datagrid->num_rows, __('Found <strong>{result->num_rows}</strong> from your keywords')); //mfc
        echo '<div class="infoBox">'.$msg.' : "'.htmlspecialchars($_GET['keywords']).'"</div>';
    }

    echo $datagrid_result;
}
/* main content end */
"""

predict_code_no_feature_cv(test)

Vulnerability Detection with Countved:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 DecisionTree results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 92.00%
   - XSS Vulnerable: 8.00%

🧪 LinearSVC results:
   - Not Vulnerable: 1.89%
   - SQL Injection Vulnerable: 94.88%
   - XSS Vulnerable: 3.23%



In [ ]:
#CVE-2025-45820
test = """
<?php
/**
 * Copyright (C) 2007,2008  Arie Nugraha (dicarve@yahoo.com)
 *
 * This program is free software; you can redistribute it and/or modify
 * it under the terms of the GNU General Public License as published by
 * the Free Software Foundation; either version 3 of the License, or
 * (at your option) any later version.
 *
 * This program is distributed in the hope that it will be useful,
 * but WITHOUT ANY WARRANTY; without even the implied warranty of
 * MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
 * GNU General Public License for more details.
 *
 * You should have received a copy of the GNU General Public License
 * along with this program; if not, write to the Free Software
 * Foundation, Inc., 51 Franklin Street, Fifth Floor, Boston, MA  02110-1301  USA
 *
 */

/* Biblio Author */

// key to authenticate
if (!defined('INDEX_AUTH')) {
  define('INDEX_AUTH', '1');
}

// main system configuration
if (!defined('SB')) {
  require '../../../sysconfig.inc.php';
}

if (isset($_GET['authorID'])) {
  $_POST['itemID'] = $_GET['authorID'];
  $_POST['detail'] = true;
}

$_GET['inPopUp'] = true;

if(isset($_POST['updateData'])){
	$biblio_id = (integer)$_POST['biblio_id'];
	$author_id = (integer)$_POST['author_id'];
	$level = (integer)$_POST['level'];
	$query = sprintf("UPDATE biblio_author SET level=%d WHERE biblio_id=%d AND author_id=%d",$level,$biblio_id,$author_id);
	$update = $dbs->query($query);
    if($update){
		utility::jsAlert('Authority Level Data Successfully Updated');
		echo '<script type="text/javascript">top.setIframeContent(\'authorIframe\', \''.MWB.'bibliography/iframe_author.php?biblioID='.$biblio_id.'\');</script>';
    	echo '<script type="text/javascript">top.jQuery.colorbox.close();</script>';
    }else {
    	utility::jsAlert( __('Authority Level Data FAILED to Updated. Please Contact System Administrator')."\nDEBUG : ".$update->error.$query);
		echo '<script type="text/javascript">top.setIframeContent(\'authorIframe\', \''.MWB.'bibliography/iframe_author.php?biblioID='.$_POST['biblioID'].'\');</script>';
    	echo '<script type="text/javascript">top.jQuery.colorbox.close();</script>';
    }
}

ob_start();

if(!isset($_GET['authority_level'])){
	require MDLBS.'master_file/author.php';
}
else{
	require SB.'admin/default/session.inc.php';
	require SB.'admin/default/session_check.inc.php';
	require SIMBIO.'simbio_GUI/table/simbio_table.inc.php';
	require SIMBIO.'simbio_GUI/form_maker/simbio_form_table_AJAX.inc.php';
	require SIMBIO.'simbio_GUI/paging/simbio_paging.inc.php';
	require SIMBIO.'simbio_DB/datagrid/simbio_dbgrid.inc.php';

    /* RECORD FORM */
    $itemID = (integer)isset($_POST['itemID'])?$_POST['itemID']:0;
    $query = 'SELECT b.biblio_id,ba.author_id,b.title,ma.author_name,ma.authority_type,ba.* FROM biblio b LEFT JOIN biblio_author ba ON ba.biblio_id=ba.biblio_id
    LEFT JOIN mst_author ma ON ma.author_id=ba.author_id WHERE b.biblio_id='.$_GET['biblio_id'].' AND ma.author_id='.$_GET['authorID'];
    $rec_q = $dbs->query($query);
    $rec_d = $rec_q->fetch_assoc();

	$form = new simbio_form_table_AJAX('authorLevelForm', $_SERVER['PHP_SELF'], 'post');
	$form->submit_button_attr = 'name="updateData" value="'.__('Update').'" class="btn btn-default"';

	// form table attributes
	$form->table_attr = 'id="dataList" class="s-table table"';
	$form->table_header_attr = 'class="alterCell font-weight-bold"';
	$form->table_content_attr = 'class="alterCell2"';

    /* Form Element(s) */
    $form->addHidden('biblio_id',$rec_d['biblio_id']);
    $form->addHidden('author_id',$rec_d['author_id']);
    // biblio title
    $form->addAnything(__('Title'),  $rec_d['title']);
    // author name
    $form->addAnything(__('Author Name'),  $rec_d['author_name']);
    // authority type
    $form->addAnything(__('Authority Type'),  $sysconf['authority_type'][$rec_d['authority_type']]);
    // authority_level
    foreach ($sysconf['authority_level'] as $authority_level_id => $authority_level) {
        $authority_level_options[] = array($authority_level_id, $authority_level);
    }
    $form->addSelectList('level', __('Authority Level'), $authority_level_options, (integer)$rec_d['level'],'class="form-control col-8"');
    // print out the form object
    echo $form->printOut();
}

$content = ob_get_clean();
// page title
$page_title = 'Biblio Author';

// include the page template
require SB.'/admin/'.$sysconf['admin_template']['dir'].'/notemplate_page_tpl.php';
"""

predict_code_no_feature_cv(test)

Vulnerability Detection with Countved:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 33.23%
   - SQL Injection Vulnerable: 33.42%
   - XSS Vulnerable: 33.35%

🧪 DecisionTree results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 2.00%
   - SQL Injection Vulnerable: 82.00%
   - XSS Vulnerable: 16.00%

🧪 LinearSVC results:
   - Not Vulnerable: 8.46%
   - SQL Injection Vulnerable: 86.41%
   - XSS Vulnerable: 5.12%



In [ ]:
random_test = """
<?php

echo $tainted;
"""

predict_code_no_feature_cv(random_test)

Vulnerability Detection with Countved:
🧪 GaussianNB results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 MultinomialNB results:
   - Not Vulnerable: 33.23%
   - SQL Injection Vulnerable: 33.42%
   - XSS Vulnerable: 33.35%

🧪 DecisionTree results:
   - Not Vulnerable: 0.00%
   - SQL Injection Vulnerable: 100.00%
   - XSS Vulnerable: 0.00%

🧪 RandomForest results:
   - Not Vulnerable: 2.00%
   - SQL Injection Vulnerable: 82.00%
   - XSS Vulnerable: 16.00%

🧪 LinearSVC results:
   - Not Vulnerable: 8.46%
   - SQL Injection Vulnerable: 86.41%
   - XSS Vulnerable: 5.12%



#countvectorizer tuned

### random forest countvec fine-tuned

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import CountVectorizer

# Tuning RandomForest
from sklearn.ensemble import RandomForestClassifier

pipeline = Pipeline([
    ('vect', CountVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';']
    )),
    ('clf', RandomForestClassifier(random_state=45, n_jobs=-1))
])

param_grid = {
    # TF-IDF parameters
    'vect__ngram_range': [(2,5), (2,7), (1,7)],
    'vect__max_df': [0.75, 1.0],
    'vect__binary': [True, False],
    # RandomForest parameters
    'clf__n_estimators': [100, 200],
    'clf__max_depth': [None, 20, 50],
    'clf__max_features': ['sqrt', 'log2'],
}

rf_grid_cv_ft = GridSearchCV(
    pipeline, param_grid,
    cv=3,
    scoring='f1_weighted',
    n_jobs=-1,
    verbose=2
)

# 1) Fit the RF grid
rf_grid_cv_ft.fit(X_train_cv['cleaned'], y_train_cv)

# 2) Inspect best params & CV score
print("Best params:", rf_grid_cv_ft.best_params_)
print("Best CV f1_weighted:", rf_grid_cv_ft.best_score_)

# 3) Evaluate on held-out test set
from sklearn.metrics import classification_report, confusion_matrix

y_pred = rf_grid_cv_ft.predict(X_test_cv['cleaned'])
print(classification_report(y_test_cv, y_pred))
print(confusion_matrix(y_test_cv, y_pred))


Fitting 3 folds for each of 144 candidates, totalling 432 fits


/usr/local/lib/python3.12/dist-packages/joblib/externals/loky/process_executor.py:782: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  warnings.warn(


Best params: {'clf__max_depth': None, 'clf__max_features': 'sqrt', 'clf__n_estimators': 200, 'vect__binary': False, 'vect__max_df': 1.0, 'vect__ngram_range': (1, 7)}
Best CV f1_weighted: 0.9808090003338491
                          precision    recall  f1-score   support

          Not Vulnerable       0.99      0.96      0.97      2429
SQL Injection Vulnerable       0.98      1.00      0.99      2375
          XSS Vulnerable       0.98      0.99      0.98      2396

                accuracy                           0.98      7200
               macro avg       0.98      0.98      0.98      7200
            weighted avg       0.98      0.98      0.98      7200

[[2323   46   60]
 [  10 2365    0]
 [  24    0 2372]]


### linear svc countvec fine-tuned

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.svm import LinearSVC
from sklearn.calibration import CalibratedClassifierCV
from sklearn.metrics import classification_report, confusion_matrix

# 1) Pipeline awal (buat GridSearch)
lsvc_pipeline = Pipeline([
    ('vect', CountVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';']
    )),
    ('clf', LinearSVC(dual=False, random_state=45))
])

# 2) Parameter grid (TETEP ADA, ga dihapus)
lsvc_param_grid = {
    'vect__ngram_range': [(2,5), (2,7)],
    'clf__C': [0.01, 0.1, 1, 10],
    'clf__max_iter': [1000, 5000]
}

# 3) GridSearchCV
lsvc_grid = GridSearchCV(
    lsvc_pipeline,
    lsvc_param_grid,
    cv=3,
    scoring='f1_weighted',
    n_jobs=-1,
    verbose=2
)

# 4) Fit GridSearch
lsvc_grid.fit(X_train_cv['cleaned'], y_train_cv)

print("Best LinearSVC params:", lsvc_grid.best_params_)
print("Best CV f1_weighted:", lsvc_grid.best_score_)

# 5) Build pipeline baru pakai CalibratedClassifierCV
best_params = lsvc_grid.best_params_

lsvc_best = LinearSVC(
    C=best_params['clf__C'],
    max_iter=best_params['clf__max_iter'],
    dual=False,
    random_state=45
)

calibrated_lsvc = CalibratedClassifierCV(
    estimator=lsvc_best,
    method='sigmoid',
    cv=3
)

calib_pipeline = Pipeline([
    ('vect', TfidfVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';'],
        ngram_range=best_params['vect__ngram_range']
    )),
    ('clf', calibrated_lsvc)
])

# 6) Fit pipeline calibrated
calib_pipeline.fit(X_train_cv['cleaned'], y_train_cv)

# 7) Evaluasi
y_pred = calib_pipeline.predict(X_test_cv['cleaned'])
print(classification_report(y_test_cv, y_pred))
print(confusion_matrix(y_test_cv, y_pred))

# probabilitas (udah bisa karena calibrated)
y_proba = calib_pipeline.predict_proba(X_test_cv['cleaned'])


Fitting 3 folds for each of 16 candidates, totalling 48 fits
Best LinearSVC params: {'clf__C': 1, 'clf__max_iter': 1000, 'vect__ngram_range': (2, 7)}
Best CV f1_weighted: 0.9846883412185647
                          precision    recall  f1-score   support

          Not Vulnerable       0.99      0.96      0.98      2429
SQL Injection Vulnerable       0.98      1.00      0.99      2375
          XSS Vulnerable       0.98      1.00      0.99      2396

                accuracy                           0.98      7200
               macro avg       0.98      0.98      0.98      7200
            weighted avg       0.98      0.98      0.98      7200

[[2328   44   57]
 [   7 2368    0]
 [   8    0 2388]]


In [ ]:
# from sklearn.pipeline import Pipeline
# from sklearn.model_selection import GridSearchCV
# from sklearn.feature_extraction.text import CountVectorizer
# from sklearn.svm import LinearSVC
# from sklearn.metrics import classification_report, confusion_matrix

# # 1) Build a fresh pipeline for LinearSVC
# lsvc_pipeline = Pipeline([
#     ('vect', CountVectorizer(
#         lowercase=False,
#         token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
#         stop_words=[';']
#     )),
#     ('clf', LinearSVC(dual=False, random_state=45))
# ])

# # 2) Define the hyper‐parameter grid
# lsvc_param_grid = {
#     'vect__ngram_range': [(2,5), (2,7)],
#     'clf__C': [0.01, 0.1, 1, 10],
#     'clf__max_iter': [1000, 5000]
# }

# # 3) Set up GridSearchCV
# lsvc_grid_cv_ft = GridSearchCV(
#     lsvc_pipeline,
#     lsvc_param_grid,
#     cv=3,
#     scoring='f1_weighted',
#     n_jobs=-1,
#     verbose=2
# )

# # 4) Fit on your full training set
# lsvc_grid_cv_ft.fit(X_train_cv['cleaned'], y_train_cv)

# # 5) Inspect best params & CV score
# print("Best LinearSVC params:", lsvc_grid_cv_ft.best_params_)
# print("Best CV f1_weighted:", lsvc_grid_cv_ft.best_score_)

# # 6) Evaluate on held-out test set
# y_pred = lsvc_grid_cv_ft.predict(X_test_cv['cleaned'])
# print(classification_report(y_test_cv, y_pred))
# print(confusion_matrix(y_test_cv, y_pred))


### gaussian naive bayes countvec fine-tuned

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.preprocessing import FunctionTransformer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import classification_report, confusion_matrix

# Tuning GaussianNB
# 1) Build a fresh pipeline
gnb_pipeline = Pipeline([
    ('vect', CountVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';']
    )),
    ('to_dense', FunctionTransformer(lambda X: X.toarray(), accept_sparse=True)),
    ('clf', GaussianNB())
])

# 2) Param grid (only var_smoothing is valid for GNB)
param_grid_gnb = {
    'vect__ngram_range': [(1,3), (2,5)],
    'vect__max_df': [0.75, 1.0],
    'clf__var_smoothing': [1e-9, 1e-8, 1e-7]
}

# 3) GridSearchCV
gnb_grid_cv_ft = GridSearchCV(
    gnb_pipeline,
    param_grid_gnb,
    cv=3,
    scoring='f1_weighted',
    n_jobs=-1,
    verbose=2,
    error_score='raise'
)

# 4) Fit
gnb_grid_cv_ft.fit(X_train_cv['cleaned'], y_train_cv)

# 5) Results
print("Best params:", gnb_grid_cv_ft.best_params_)
print("Best CV f1_weighted:", gnb_grid_cv_ft.best_score_)

# 6) Test-set performance
y_pred = gnb_grid_cv_ft.predict(X_test_cv['cleaned'])
print(classification_report(y_test_cv, y_pred))
print(confusion_matrix(y_test_cv, y_pred))


Fitting 3 folds for each of 12 candidates, totalling 36 fits
Best params: {'clf__var_smoothing': 1e-09, 'vect__max_df': 1.0, 'vect__ngram_range': (2, 5)}
Best CV f1_weighted: 0.959810920937127
                          precision    recall  f1-score   support

          Not Vulnerable       1.00      0.89      0.94      2429
SQL Injection Vulnerable       0.94      1.00      0.97      2375
          XSS Vulnerable       0.96      1.00      0.98      2396

                accuracy                           0.96      7200
               macro avg       0.96      0.96      0.96      7200
            weighted avg       0.96      0.96      0.96      7200

[[2156  162  111]
 [   4 2371    0]
 [   1    0 2395]]


### multinomial naive bayes countvec fine-tuned

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import classification_report, confusion_matrix

# Tuning MNB
# 1) Define the pipeline
mnb_pipeline = Pipeline([
    ('vect', CountVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';']
    )),
    ('clf', MultinomialNB())
])

# 2) Define hyperparameter grid
mnb_param_grid = {
    'vect__ngram_range': [(1,3), (2,5)],
    'clf__alpha': [0.1, 0.5, 1.0]
}

# 3) Setup GridSearchCV
mnb_grid_cv_ft = GridSearchCV(
    mnb_pipeline,
    mnb_param_grid,
    cv=3,
    scoring='f1_weighted',
    n_jobs=-1,
    verbose=2
)

# 4) Train the model
mnb_grid_cv_ft.fit(X_train_cv['cleaned'], y_train_cv)

# 5) Output best params and score
print("Best MultinomialNB params:", mnb_grid_cv_ft.best_params_)
print("Best CV f1_weighted:", mnb_grid_cv_ft.best_score_)

# 6) Evaluate on test data
y_pred = mnb_grid_cv_ft.predict(X_test_cv['cleaned'])
print(classification_report(y_test_cv, y_pred))
print(confusion_matrix(y_test_cv, y_pred))


Fitting 3 folds for each of 6 candidates, totalling 18 fits
Best MultinomialNB params: {'clf__alpha': 0.1, 'vect__ngram_range': (2, 5)}
Best CV f1_weighted: 0.9336584087451169
                          precision    recall  f1-score   support

          Not Vulnerable       1.00      0.83      0.91      2429
SQL Injection Vulnerable       0.93      1.00      0.97      2375
          XSS Vulnerable       0.91      1.00      0.95      2396

                accuracy                           0.94      7200
               macro avg       0.95      0.94      0.94      7200
            weighted avg       0.95      0.94      0.94      7200

[[2026  168  235]
 [   0 2375    0]
 [   0    0 2396]]


### decision tree countvec fine-tuned

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import classification_report, confusion_matrix

# Tuning Decision Tree
# 1) Build a fresh pipeline
dtc_pipeline = Pipeline([
    ('vect', CountVectorizer(
        lowercase=False,
        token_pattern='[a-zA-Z0-9$&+,:;=?@{}_|<>.^*()%!-]+',
        stop_words=[';']
    )),
    ('clf', DecisionTreeClassifier(random_state=45))
])

# 2) Param grid for Decision Tree
param_grid_dtc = {
    'vect__ngram_range': [(1,3), (2,5)],
    'vect__max_df': [0.75, 1.0],
    'clf__max_depth': [None, 10, 20, 50],
    'clf__min_samples_split': [2, 5, 10],
    'clf__criterion': ['gini', 'entropy']
}

# 3) GridSearchCV
dtc_grid_cv_ft = GridSearchCV(
    dtc_pipeline,
    param_grid_dtc,
    cv=3,
    scoring='f1_weighted',
    n_jobs=-1,
    verbose=2,
    error_score='raise'
)

# 4) Fit
dtc_grid_cv_ft.fit(X_train_cv['cleaned'], y_train_cv)

# 5) Results
print("Best params:", dtc_grid_cv_ft.best_params_)
print("Best CV f1_weighted:", dtc_grid_cv_ft.best_score_)

# 6) Test-set performance
y_pred = dtc_grid_cv_ft.predict(X_test_cv['cleaned'])
print(classification_report(y_test_cv, y_pred))
print(confusion_matrix(y_test_cv, y_pred))


Fitting 3 folds for each of 96 candidates, totalling 288 fits
Best params: {'clf__criterion': 'gini', 'clf__max_depth': 50, 'clf__min_samples_split': 10, 'vect__max_df': 0.75, 'vect__ngram_range': (1, 3)}
Best CV f1_weighted: 0.9833484591549476
                          precision    recall  f1-score   support

          Not Vulnerable       0.99      0.97      0.98      2429
SQL Injection Vulnerable       0.99      1.00      0.99      2375
          XSS Vulnerable       0.98      0.99      0.99      2396

                accuracy                           0.99      7200
               macro avg       0.99      0.99      0.99      7200
            weighted avg       0.99      0.99      0.99      7200

[[2345   36   48]
 [   5 2370    0]
 [  12    0 2384]]


# exporting countvec all

In [ ]:
import os
import cloudpickle

# Base directory on Google Drive
BASE_DIR = '/content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_cv'
os.makedirs(BASE_DIR, exist_ok=True)

# Map short names to your trained models with CountVectorizer
models_to_save = {
    'gnb_model_FIN_CV'  : GNB_vec_cv,
    'mnb_model_FIN_CV'  : MNB_vec_cv,
    'dtc_model_FIN_CV'  : DTC_vec_cv,
    'rf_model_FIN_CV'   : RFC_vec_cv,
    'lsvc_model_FIN_CV': LSVC_vec_cv,
    'count_vect_FIN_CV' : vecto_cv  # Save the CountVectorizer too
}

# Dump each with cloudpickle
for name, model in models_to_save.items():
    path = os.path.join(BASE_DIR, f'{name}.pkl')
    with open(path, 'wb') as f:
        cloudpickle.dump(model, f)
    print(f"Saved {path}")


Saved /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_cv/gnb_model_FIN_CV.pkl
Saved /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_cv/mnb_model_FIN_CV.pkl
Saved /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_cv/dtc_model_FIN_CV.pkl
Saved /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_cv/rf_model_FIN_CV.pkl
Saved /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_cv/lsvc_model_FIN_CV.pkl
Saved /content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_cv/count_vect_FIN_CV.pkl


In [ ]:
import os
import cloudpickle

# Base directory on Google Drive
BASE_DIR = '/content/drive/MyDrive/REVISI_NEW_MODEL/tuned_cv'
os.makedirs(BASE_DIR, exist_ok=True)


model_dict = {
    'gnb_pipeline_FINTUN_cv': gnb_grid_cv_ft.best_estimator_,
    'mnb_pipeline_FINTUN_cv': mnb_grid_cv_ft.best_estimator_,
    'dtc_pipeline_FINTUN_cv': dtc_grid_cv_ft.best_estimator_,
    'rf_pipeline_FINTUN_cv': rf_grid_cv_ft.best_estimator_,
    'lsvc_pipeline_FINTUN_cv': lsvc_grid_cv_ft.best_estimator_,
}

for name, pipeline in model_dict.items():
    # 1. Save full pipeline
    pipeline_path = os.path.join(BASE_DIR, f'{name}.pkl')
    with open(pipeline_path, 'wb') as f:
        cloudpickle.dump(pipeline, f)
    print(f"✅ Saved pipeline → {pipeline_path}")

    # 2. Save vectorizer from the pipeline
    vect = pipeline.named_steps['vect']
    vect_path = os.path.join(BASE_DIR, f'vect_cv_ft_{name}.pkl')
    with open(vect_path, 'wb') as f:
        cloudpickle.dump(vect, f)
    print(f"✅ Saved vectorizer → {vect_path}")

In [ ]:
import cloudpickle

def predict_code_finetuned_cv(code_input: str):
    BASE_PATH = "/content/drive/MyDrive/REVISI_NEW_MODEL/tuned_cv"

    # Load fine-tuned pipelines (CV version)
    gnb_model = cloudpickle.load(open(f"{BASE_PATH}/gnb_pipeline_FINTUN_cv.pkl", "rb"))
    mnb_model = cloudpickle.load(open(f"{BASE_PATH}/mnb_pipeline_FINTUN_cv.pkl", "rb"))
    dtc_model = cloudpickle.load(open(f"{BASE_PATH}/dtc_pipeline_FINTUN_cv.pkl", "rb"))
    rf_model  = cloudpickle.load(open(f"{BASE_PATH}/rf_pipeline_FINTUN_cv.pkl", "rb"))
    lsvc_model = cloudpickle.load(open(f"{BASE_PATH}/lsvc_pipeline_FINTUN_cv.pkl", "rb"))

    # Load matching vectorizers
    gnb_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_cv_ft_gnb_pipeline_FINTUN_cv.pkl", "rb"))
    mnb_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_cv_ft_mnb_pipeline_FINTUN_cv.pkl", "rb"))
    dtc_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_cv_ft_dtc_pipeline_FINTUN_cv.pkl", "rb"))
    rf_vectorizer  = cloudpickle.load(open(f"{BASE_PATH}/vect_cv_ft_rf_pipeline_FINTUN_cv.pkl", "rb"))
    lsvc_vectorizer = cloudpickle.load(open(f"{BASE_PATH}/vect_cv_ft_lsvc_pipeline_FINTUN_cv.pkl", "rb"))

    # Preprocess input
    processed = str(process_php_tokenized(code_input))

    # Vectorize per model
    gnb_X = gnb_vectorizer.transform([processed]).toarray()
    mnb_X = mnb_vectorizer.transform([processed])
    dtc_X = dtc_vectorizer.transform([processed])
    rf_X  = rf_vectorizer.transform([processed])
    lsvc_X = lsvc_vectorizer.transform([processed])

    # Predict
    print("🔍 Prediksi Fine-tuned CountVectorizer models:")
    print("🧪 GaussianNB       :", gnb_model.predict([processed])[0])
    print("🧪 MultinomialNB    :", mnb_model.predict([processed])[0])
    print("🧪 DecisionTree     :", dtc_model.predict([processed])[0])
    print("🧪 RandomForest     :", rf_model.predict([processed])[0])
    print("🧪 LinearSVC        :", lsvc_model.predict([processed])[0])


In [ ]:
code_sample = """
<?php

system($_GET['cmd']);

?>
"""

predict_code_finetuned_cv(code_sample)


In [ ]:
import cloudpickle

def predict_code_nontuned_cv(code_input: str):
    BASE_PATH = "/content/drive/MyDrive/REVISI_NEW_MODEL/nottuned_cv"

    # Load models
    gnb_model = cloudpickle.load(open(f"{BASE_PATH}/gnb_model_FIN_CV.pkl", "rb"))
    mnb_model = cloudpickle.load(open(f"{BASE_PATH}/mnb_model_FIN_CV.pkl", "rb"))
    dtc_model = cloudpickle.load(open(f"{BASE_PATH}/dtc_model_FIN_CV.pkl", "rb"))
    rf_model  = cloudpickle.load(open(f"{BASE_PATH}/rf_model_FIN_CV.pkl", "rb"))
    lsvc_model = cloudpickle.load(open(f"{BASE_PATH}/lsvc_model_FIN_CV.pkl", "rb"))

    # Load vectorizer
    vectorizer = cloudpickle.load(open(f"{BASE_PATH}/count_vect_FIN_CV.pkl", "rb"))

    # Preprocess input
    processed = str(process_php_tokenized(code_input))

    # Transform input
    X_input = vectorizer.transform([processed])
    X_dense = X_input.toarray()  # for GNB

    # Predict
    print("🔍 Prediksi CountVectorizer (non-tuned):")
    print("🧪 GaussianNB       :", gnb_model.predict(X_dense)[0])
    print("🧪 MultinomialNB    :", mnb_model.predict(X_input)[0])
    print("🧪 DecisionTree     :", dtc_model.predict(X_input)[0])
    print("🧪 RandomForest     :", rf_model.predict(X_input)[0])
    print("🧪 LinearSVC        :", lsvc_model.predict(X_input)[0])


In [ ]:
code_sample = """
<?php

system($_GET['cmd']);

?>
"""

predict_code_nontuned_cv(code_sample)